# Instructions

* This notebook is refered to MScFE 690 Capstone - Module 7 and it is finished and running succefully, for an ongoing updated code go to the vLive version.
* Since the notebook requires the instalation of modules it is required to restart the sessions afer the modules are installed.


In [1]:
import requests
import pandas as pd
import os
import time
from datetime import date, datetime, timedelta
import json
import re
import yfinance as yf

import matplotlib.pyplot as plt
import plotly.express as px
import plotly.colors as pc
import plotly.graph_objects as go
import matplotlib.dates as mdates
from scipy.optimize import minimize
from plotly.subplots import make_subplots

from plotly.subplots import make_subplots
import os
import requests
import numpy as np

try:
  import quiverquant
except:
  !pip install quiverquant
  import quiverquant

import warnings
warnings.simplefilter(action='ignore', category=FutureWarning)


In [2]:
# Create output directory
os.makedirs("data", exist_ok=True)

# Data collection

## Configuration

In [3]:
POLYGON_KEY = "ft2rquZoprD0MSBmJqQfD_8qNsxrkK_1"
QUIVER_TOKEN = "a8dcf66a9fd588b78513ccedb4b92acc948ac6e3"

In [4]:
# Get the directory of this script
SCRIPT_DIR = os.getcwd()
# Congressional term date ranges
CONGRESS_START_DATE = "2019-01-03"  # 116th Congress start
CONGRESS_END_DATE = "2025-01-02"    # 118th Congress end

# Major economic states for geographic filtering
MAJOR_STATES = ['CA', 'NY', 'TX', 'FL', 'IL', 'PA', 'OH', 'GA', 'NC', 'MI',
                'NJ', 'VA', 'WA', 'AZ', 'MA', 'TN', 'CO', 'MD', 'CT', 'AL']

# Output directory
OUTPUT_DIR = os.path.join(SCRIPT_DIR, 'output')
os.makedirs(OUTPUT_DIR, exist_ok=True)

In [5]:
BACKTEST_START_DATE = '2025-01-03'
BACKTEST_END_DATE = '2025-12-31'
BACKTEST_OUTPUT_DIR = os.path.join(SCRIPT_DIR, 'output/backtest/')
os.makedirs(BACKTEST_OUTPUT_DIR, exist_ok=True)

In [6]:
lawmakers = [
    # --- Senators ---
    # {"name": "Ron Wyden", "party": "Democratic", "chamber": "Senate", "state": "OR", "bioguide": "W000779"},
    # {"name": "Thomas R. Carper", "party": "Democratic", "chamber": "Senate", "state": "DE", "bioguide": "C000174"},
    # {"name": "A. Mitchell Jr. McConnell", "party": "Republican", "chamber": "Senate", "state": "KY", "bioguide": "M000355"},

    # # --- House of Representatives ---

    {"name": "Josh Gottheimer", "party": "Democratic", "chamber": "House", "state": "NJ", "bioguide": "G000583"},
    {"name": "Nancy Pelosi", "party": "Democratic", "chamber": "House", "state": "CA", "bioguide": "P000197"},
    {"name": "Kevin Hern", "party": "Republican", "chamber": "House", "state": "OK", "bioguide": "H001082"},
    {"name": "Mark Green", "party": "Republican", "chamber": "House", "state": "TN", "bioguide": "G000590"},
    {"name": "Bradley S. Schneider", "party": "Democratic", "chamber": "House", "state": "IL", "bioguide": "S001190"},
    {"name": "Virginia Foxx", "party": "Republican", "chamber": "House", "state": "NC", "bioguide": "F000450"},
    {"name": "Kim Schrier", "party": "Democratic", "chamber": "House", "state": "WA", "bioguide": "S001216"},
    {"name": "Mikie Sherrill", "party": "Democratic", "chamber": "House", "state": "NJ", "bioguide": "S001207"},
    {"name": "Daniel Meuser", "party": "Republican", "chamber": "House", "state": "PA", "bioguide": "M001204"},
    {"name": "Susie Lee", "party": "Democratic", "chamber": "House", "state": "NV", "bioguide": "L000590"},
    {"name": "John W. Rose", "party": "Republican", "chamber": "House", "state": "TN", "bioguide": "R000612"},
    {"name": "Brian Mast", "party": "Republican", "chamber": "House", "state": "FL", "bioguide": "M001199"},
    {"name": "Carol Devine Miller", "party": "Republican", "chamber": "House", "state": "WV", "bioguide": "M001205"},
    {"name": "Michael C. Burgess", "party": "Republican", "chamber": "House", "state": "TX", "bioguide": "B001248"},
    {"name": "Pete Sessions", "party": "Republican", "chamber": "House", "state": "TX", "bioguide": "S000250"},
    {"name": "Lois Frankel", "party": "Democratic", "chamber": "House", "state": "FL", "bioguide": "F000462"},
    {"name": "Earl Blumenauer", "party": "Democratic", "chamber": "House", "state": "OR", "bioguide": "B000574"},
    {"name": "Michael Garcia", "party": "Republican", "chamber": "House", "state": "CA", "bioguide": "G000061"},
    {"name": "Donald Sternoff Beyer Jr", "party": "Democratic", "chamber": "House", "state": "VI", "bioguide": "B001292"},
    {"name": "Debbie Dingell", "party": "Democratic", "chamber": "House", "state": "MI", "bioguide": "D000624"},

]
lawmakers = pd.DataFrame(lawmakers)
lawmakers.to_csv("data/lawmakers.csv", index=False)



## Yfinance data

In [7]:
# 1. Fetch Data
ticker = "NVDA"
df = yf.download(ticker, period="1y", interval="1d")
df = df.stack(level='Ticker').reset_index()

# 2. Create Subplots (2 Rows: Price on top, Volume on bottom)
# row_heights=[0.7, 0.3] gives 70% space to Price, 30% to Volume
fig = make_subplots(
    rows=2, cols=1,
    shared_xaxes=True,
    vertical_spacing=0.03,
    subplot_titles=(f'{ticker} Price', 'Volume'),
    row_heights=[0.7, 0.3]
)

# 3. Add Candlestick Trace (Row 1)
fig.add_trace(go.Candlestick(
    x=df.Date,
    open=df['Open'],
    high=df['High'],
    low=df['Low'],
    close=df['Close'],
    name='Price'
), row=1, col=1)

# 4. Add Volume Trace (Row 2)
# We color the volume bars based on price change (Green for up, Red for down)
colors = ['green' if row['Open'] - row['Close'] >= 0
          else 'red' for index, row in df.iterrows()]

fig.add_trace(go.Bar(
    x=df.Date,
    y=df['Volume'],
    marker_color=colors,
    name='Volume'
), row=2, col=1)

# 5. Add Moving Average (Optional, on Row 1)
df['MA20'] = df['Close'].rolling(window=20).mean()
fig.add_trace(go.Scatter(
    x=df.Date,
    y=df['MA20'],
    line=dict(color='orange', width=2),
    name='20-Day MA'
), row=1, col=1)

# 6. Final Layout Adjustments
fig.update_layout(
    title=f'{ticker} Candlestick Chart with Volume',
    template='plotly_dark',
    xaxis_rangeslider_visible=False, # Hides the slider (redundant with zoom)
    height=800 # Taller figure to accommodate both plots
)

# Show the Plot
fig.show()

[*********************100%***********************]  1 of 1 completed


In [8]:
df = yf.download(ticker, period="1y", interval="1d", ignore_tz=True)

[*********************100%***********************]  1 of 1 completed


In [9]:
clean_df = df.stack(level='Ticker').reset_index()
clean_df.head()

Price       Date Ticker       Close        High         Low        Open  \
0     2025-02-26   NVDA  131.244110  133.693437  128.454880  129.954469   
1     2025-02-27   NVDA  120.117149  134.973079  119.977188  134.963087   
2     2025-02-28   NVDA  124.885841  125.055793  116.368174  117.987727   
3     2025-03-03   NVDA  114.028809  123.666172  112.249297  123.476229   
4     2025-03-04   NVDA  115.958282  119.277374  110.079893  110.619746   

Price     Volume  
0      322553800  
1      443175800  
2      389091100  
3      411381400  
4      398163300

## Quiver transaction history

In [10]:
class CustomQuiver(quiverquant.quiver):

    def congress_trading(self, ticker="", politician=True, recent=False, representative="", bioguide=""):


      if recent:
          urlStart = 'https://api.quiverquant.com/beta/live/congresstrading'
      else:
          urlStart = 'https://api.quiverquant.com/beta/bulk/congresstrading'

      if politician:
          representative = representative.replace(" ", "%20")
          ticker = ticker.replace(" ", "%20")

          if representative:
            url = urlStart+"?representative="+representative+ticker

          elif bioguide:
            url = urlStart+"?bioguide_id="+bioguide+ticker


      elif len(ticker)>0:
          url = urlStart+"/"+ticker
      else:
          url = urlStart
      print(url)
      r = requests.get(url, headers=self.headers)
      j = json.loads(r.content)
      df = pd.DataFrame(j)
      return df

# === API KEYS  ===
# - Quiver Quantitative: https://www.quiverquant.com/ (paid subscription required for API access, but has free trial)
# - Documentation on https://api.quiverquant.com/docs/#/ and https://github.com/Quiver-Quantitative/python-api

QUIVER_TOKEN = "a8dcf66a9fd588b78513ccedb4b92acc948ac6e3"

# # 1 Initialize Quiver client (token required for full access)

# qq = quiverquant.quiver(QUIVER_TOKEN)

quiver = CustomQuiver(QUIVER_TOKEN)


In [11]:
def fetch_congress_trading(use_cache=True, cache_file=None):
    """
    Fetch all congress trading data from Quiver API.

    Parameters:
    -----------
    use_cache : bool
        If True, use cached data if available
    cache_file : str
        Path to cache file

    Returns:
    --------
    pd.DataFrame : All congress trading records
    """
    if cache_file is None:
        cache_file = os.path.join(OUTPUT_DIR, 'raw_congress_trades.csv')

    # Check cache
    if use_cache and os.path.exists(cache_file):
        print(f"Loading cached data from {cache_file}")
        df = pd.read_csv(cache_file)
        return df

    # Fetch from API
    print("Fetching congress trading data from Quiver API...")
    quiver = CustomQuiver(QUIVER_TOKEN)
    df = quiver.congress_trading(recent=False, politician=False)

    # Save cache
    df.to_csv(cache_file, index=False)
    print(f"Saved {len(df)} records to {cache_file}")

    return df

In [12]:
raw_df = fetch_congress_trading(use_cache=True)

Loading cached data from c:\Users\Aaron\Documents\Projects\WQU\Capston_Project\Congress_Trading\output\raw_congress_trades.csv


C:\Users\Aaron\AppData\Local\Temp\ipykernel_6424\1314346047.py:22: DtypeWarning:

Columns (5) have mixed types. Specify dtype option on import or set low_memory=False.



In [13]:
def filter_by_date_range(df, start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE):
    """
    Filter trading data to specified date range.

    Parameters:
    -----------
    df : pd.DataFrame
        Trading data
    start_date : str
        Start date (YYYY-MM-DD)
    end_date : str
        End date (YYYY-MM-DD)

    Returns:
    --------
    pd.DataFrame : Filtered data
    """
    df_filtered = df.loc[
        (df['Traded'] >= start_date) &
        (df['Traded'] <= end_date)
    ].copy()

    print(f"Filtered to {len(df_filtered)} records between {start_date} and {end_date}")
    return df_filtered


In [14]:
def clean_trading_data(df):
    """
    Clean and preprocess trading data.

    Parameters:
    -----------
    df : pd.DataFrame
        Raw trading data

    Returns:
    --------
    pd.DataFrame : Cleaned data
    """
    df = df.copy()

    # Convert numeric columns
    df['Trade_Size_USD'] = pd.to_numeric(df['Trade_Size_USD'], errors='coerce')
    df['excess_return'] = pd.to_numeric(df['excess_return'], errors='coerce')

    # Drop rows with missing critical values
    df = df.dropna(subset=['Trade_Size_USD', 'excess_return'])

    # Filter out non-positive trade sizes
    df = df[df['Trade_Size_USD'] > 0]

    # Convert dates
    df['Traded'] = pd.to_datetime(df['Traded'])
    df['Filed'] = pd.to_datetime(df['Filed'], errors='coerce')

    # Extract state from District (e.g., 'CA11' -> 'CA')
    df['State'] = df['District'].astype(str).str.strip().str.extract(r'([A-Z]{2})', expand=False)

    # Add year column for yearly analysis
    df['Year'] = df['Traded'].dt.year

    print(f"Cleaned data: {len(df)} records, {df['Name'].nunique()} unique politicians")
    return df



In [15]:
df_date_filtered = filter_by_date_range(raw_df)

Filtered to 56932 records between 2019-01-03 and 2025-01-02


In [16]:
cleaned_df = clean_trading_data(df_date_filtered)

Cleaned data: 52707 records, 244 unique politicians


# EDA

In [17]:
class Congressman:
  def __init__(self, name:str, party:str, chamber:str, state:str, bioguide:str, quiverClient):

    self.name = name
    self.party = party
    self.chamber = chamber
    self.state = state
    self.bioguide = bioguide
# -------------

    self.transactions = self.get_transactions(quiverClient)
    self.tickers = self.get_tickers()

    self.positions = self.get_positions()
    self.positions45days = self.get_positions(delay=True)

    self.portfolio = None
    self.portfolio45days = None

    self.weights = None
    self.weights45days = None

    self.returns = None
    self.returns45days = None

  def get_transactions(self, quiverClient):

    transactions = quiverClient.congress_trading(bioguide=self.bioguide)
    if transactions.empty:
        print("No transacction history for ", self.name)
        return None

    transactions = transactions[~transactions['TickerType'].str.contains('OP|None', na=True)]
    transactions = transactions[['Ticker', 'TickerType', 'Traded', 'Transaction', 'Description', 'Filed', 'Trade_Size_USD']]

    # Removing options trades
    transactions = transactions[~transactions['Description'].str.contains('options', na=False, case=False)]

    transactions['Trade_Size_USD'] = transactions['Trade_Size_USD'].str.extract(r'(\d{1,3}(?:,\d{3})*)', expand=False)

    # Remove commas from the extracted strings and convert to a numeric type (float)
    # Errors='coerce' will turn values that can't be converted into NaN
    transactions['Trade_Size_USD'] = transactions['Trade_Size_USD'].str.replace(',', '', regex=False).astype(float)

    transactions['Transaction'] = transactions['Transaction'].map({"Purchase": 1, "Sale": -1})
    transactions['Transaction'].dropna

    transactions['Trade_Size_USD'] = transactions['Trade_Size_USD'] * transactions['Transaction']

    transactions["Traded"] = pd.to_datetime(transactions["Traded"])
    transactions = transactions.set_index('Traded')

    return transactions

  def get_tickers(self):

    tickers = self.transactions['Ticker'].unique().tolist()

    # Mapping for known ticker changes (keep this)
    ticker_mapping = {'FB': 'META'}  # add more if needed
    tickers = [ticker_mapping.get(t, t) for t in tickers]

    # Strict filter: only allow typical US stock ticker patterns
    # - Uppercase letters, numbers, and dots (for class shares like BRK.B)
    # - No spaces, no commas, no lowercase, reasonable length
    def is_valid_ticker(t):
        return (
            bool(re.fullmatch(r'[A-Z0-9\.]{1,10}', t)) and
            ' ' not in t and
            ',' not in t and
            t.isupper()
        )

    valid_tickers = [t for t in tickers if is_valid_ticker(t)]

    manual_excludes = {'BFET', 'WORK', 'VSNT'}
    valid_tickers = [t for t in valid_tickers if t not in manual_excludes]

    print(valid_tickers)
    return valid_tickers

  def get_positions(self, delay=False):

    if self.transactions.empty:
      # Fallback empty DataFrame
      print('No positions for: ', self.name)
      return pd.DataFrame(columns=self.tickers)

    trans = self.transactions.copy()

    # Apply 45-day delay if requested
    trade_date_col = "Traded"  # default uses original index

    if delay:
        print(f"Delayed for: {self.name}")
        trans['TradedDelay45'] = trans.index + pd.Timedelta(days=45)
        trade_date_col = "TradedDelay45"

    # Daily net dollar flows by ticker
    daily_delta = trans.pivot_table(
        index=trade_date_col,
        columns="Ticker",
        values="Trade_Size_USD",
        aggfunc="sum"
    ).sort_index()

    print(f"Daily delta for {self.name}:")
    positions = daily_delta.cumsum()

    full_index = pd.date_range(
        start=positions.index.min(),
        end=positions.index.max(),
        freq="D"
    )

    # Reindex to daily, forward-fill holdings, zero before first trade
    positions = (
        positions
        .reindex(full_index)
        .ffill()
        .fillna(0)
    )

    start_date_str = '2019-01-03'
    end_date_str = '2025-01-03'
    start = date.fromisoformat(start_date_str)
    end = date.fromisoformat(end_date_str)

    # Final safety: only our tickers, sorted columns
    target_index = pd.date_range(start=start, end=end, freq='D')
    positions = positions.reindex(target_index)

    positions = positions.loc[:, positions.columns.isin(self.tickers)]

    return positions

# -----

lawmakers_test = [
    # --- Senators ---
    {"name": "Mitch McConnell", "party": "Republican", "chamber": "Senate", "state": "KY", "bioguide": "M000355"},
    {"name": "Nancy Pelosi", "party": "Democrat", "chamber": "House", "state": "CA", "bioguide": "P000197"},
    {"name": "Ted Cruz", "party": "Republican", "chamber": "Senate", "state": "TX", "bioguide": "C001098"},  # state fixed from "ME"
  ]

congressmen = []

for l in lawmakers_test:
    congressman = Congressman(
        name=l["name"],
        party=l["party"],
        chamber=l["chamber"],
        state=l["state"],
        bioguide=l["bioguide"],
        quiverClient=quiver
    )
    congressmen.append(congressman)



all_tickers = [ticker for c in congressmen for ticker in c.tickers]
unique_tickers = list(set(all_tickers))  # removes duplicates
unique_tickers.sort()                    # optional: alphabetical order


def get_prices(tickers):
  start_date_str = '2019-01-03'
  end_date_str = '2025-01-03'
  start_date = date.fromisoformat(start_date_str)
  end_date = date.fromisoformat(end_date_str)

  all_ticker_prices = {}

  if tickers:
      print(f"Downloading prices for {len(tickers)} tickers...")
      prices_multi = yf.download(
          tickers,
          start=start_date_str,
          end=end_date_str,
          interval='1d',
          auto_adjust=True,
          progress=True
      )

      # prices_multi['Close'] is a DataFrame with columns = tickers
      close_df = prices_multi['Close']

      for ticker in tickers:
          series = close_df[ticker]
          if series.notna().any():  # has at least some real data
              all_ticker_prices[ticker] = series
          else:
              print(f"No valid price data for {ticker}")

  else:
      print("No valid tickers found.")

  # Create a master DataFrame with a full date range
  full_date_range = pd.date_range(start=start_date_str, end=end_date_str, freq='D')
  prices_df = pd.DataFrame(index=full_date_range)

  # Populate the master DataFrame with ticker prices
  for ticker, prices_series in all_ticker_prices.items():
      prices_df[ticker] = prices_series

  prices_df = prices_df.dropna(how='all')
  prices_df = prices_df.fillna(0)

  return prices_df

prices = get_prices(unique_tickers)
print(prices)


https://api.quiverquant.com/beta/bulk/congresstrading?bioguide_id=M000355
['LAZR', 'WFC', 'KR', 'VMC', 'IR']
Daily delta for Mitch McConnell:
Delayed for: Mitch McConnell
Daily delta for Mitch McConnell:
https://api.quiverquant.com/beta/bulk/congresstrading?bioguide_id=P000197
['AB', 'DIS', 'GOOGL', 'AAPL', 'PYPL', 'NVDA', 'AMZN', 'MSFT', 'V', 'TSLA', 'NFLX', 'RBLX', 'WBD', 'CRWD', 'META', 'MORN', 'IBKR', 'T']
Daily delta for Nancy Pelosi:
Delayed for: Nancy Pelosi
Daily delta for Nancy Pelosi:
https://api.quiverquant.com/beta/bulk/congresstrading?bioguide_id=C001098


[***                    7%                       ]  2 of 27 completed

['GS', 'BTC', 'PAGP', 'OKE']
Daily delta for Ted Cruz:
Delayed for: Ted Cruz
Daily delta for Ted Cruz:


[*********************100%***********************]  27 of 27 completed

1 Failed download:
['LAZR']: YFPricesMissingError('possibly delisted; no price data found  (1d 2019-01-03 -> 2025-01-03) (Yahoo error = "No data found, symbol may be delisted")')


No valid price data for LAZR
                  AAPL         AB        AMZN        BTC        CRWD  \
2019-01-03   33.768082  14.834598   75.014000   0.000000    0.000000   
2019-01-04   35.209610  15.174817   78.769501   0.000000    0.000000   
2019-01-07   35.131245  15.099216   81.475502   0.000000    0.000000   
2019-01-08   35.800953  15.174817   82.829002   0.000000    0.000000   
2019-01-09   36.408916  15.153217   82.971001   0.000000    0.000000   
...                ...        ...         ...        ...         ...   
2024-12-26  257.612732  33.434402  227.050003  42.330002  365.079987   
2024-12-27  254.201370  33.282467  223.750000  41.820000  354.989990   
2024-12-30  250.829788  32.585354  221.300003  41.750000  349.309998   
2024-12-31  249.059464  33.148411  219.389999  41.869999  342.160004   
2025-01-02  242.525162  33.121597  220.220001  43.160000  347.339996   

                   DIS       GOOGL          GS       IBKR         IR  ...  \
2019-01-03  102.629349   50.8

# Analysis

In [18]:
INITIAL_CAPITAL = 100000  # For normalization

# Data file paths
RAW_TRADES_PATH = './output/raw_congress_trades.csv'
LAWMAKERS_PATH = './data/lawmakers.csv'

# Snapshot dates for pie charts
SNAPSHOT_DATES = [
    '2019-01-03',  # Start
    '2019-12-31',  # Year-end 2019
    '2020-12-31',  # Year-end 2020
    '2021-12-31',  # Year-end 2021
    '2022-12-31',  # Year-end 2022
    '2023-12-31',  # Year-end 2023
    '2024-12-31',  # Year-end 2024
    '2025-01-02',  # End
]


In [19]:
cleaned_df.columns

Index(['Ticker', 'TickerType', 'Company', 'Traded', 'Transaction',
       'Trade_Size_USD', 'Status', 'Subholding', 'Description', 'Name',
       'BioGuideID', 'Filed', 'Party', 'District', 'Chamber', 'Comments',
       'Quiver_Upload_Time', 'excess_return', 'State', 'last_modified',
       'Year'],
      dtype='object')

In [20]:
class Congressman_df:
    """Represents a legislator with their trading history and positions.

    Uses pre-loaded DataFrame instead of API calls.
    """

    def __init__(self, name: str, party: str, chamber: str, state: str,
                 bioguide: str, trades_df: pd.DataFrame):
        self.name = name
        self.party = party
        self.chamber = chamber
        self.state = state
        self.bioguide = bioguide

        self.transactions = self._get_transactions(trades_df)
        self.tickers = self._get_tickers() if self.transactions is not None else []
        self.positions_df = self._build_positions_df() if self.transactions is not None else pd.DataFrame()

    def _get_transactions(self, trades_df: pd.DataFrame):
        """Filter and clean transaction history from DataFrame."""
        try:
            # Filter by BioGuideID
            transactions = trades_df[trades_df['BioGuideID'] == self.bioguide].copy()

            if transactions.empty:
                # Try by name as fallback
                transactions = trades_df[trades_df['Name'] == self.name].copy()

            if transactions.empty:
                print(f"No transactions found for {self.name}")
                return None

            # Filter out options and non-stock trades
            if 'TickerType' in transactions.columns:
                transactions = transactions[~transactions['TickerType'].str.contains('OP|None', na=True)]

            # Keep relevant columns
            keep_cols = ['Ticker', 'TickerType', 'Traded', 'Transaction',
                         'Description', 'Filed', 'Trade_Size_USD']
            available_cols = [c for c in keep_cols if c in transactions.columns]
            transactions = transactions[available_cols].copy()

            # Filter out options from description
            if 'Description' in transactions.columns:
                transactions = transactions[~transactions['Description'].str.contains('options', na=False, case=False)]

            # Parse trade size - handle both string and numeric values
            transactions['Trade_Size_USD'] = pd.to_numeric(transactions['Trade_Size_USD'], errors='coerce')

            # Convert dates
            transactions['Traded'] = pd.to_datetime(transactions['Traded'])
            transactions['Filed'] = pd.to_datetime(transactions['Filed'])

            # Drop rows with missing trade size
            # transactions = transactions.dropna(subset=['Trade_Size_USD'])

            return transactions.sort_values('Traded').reset_index(drop=True)

        except Exception as e:
            print(f"Error processing transactions for {self.name}: {e}")
            return None

    def _get_tickers(self):
        """Extract unique valid stock tickers."""
        if self.transactions is None:
            return []

        tickers = self.transactions['Ticker'].unique().tolist()

        # Mapping for known ticker changes
        ticker_mapping = {'FB': 'META'}
        tickers = [ticker_mapping.get(t, t) for t in tickers]

        # Validate ticker format
        def is_valid_ticker(t):
            return (
                bool(re.fullmatch(r'[A-Z0-9\.]{1,10}', str(t))) and
                ' ' not in str(t) and
                ',' not in str(t) and
                str(t).isupper()
            )

        valid_tickers = [t for t in tickers if is_valid_ticker(t)]
        return valid_tickers

    def _build_positions_df(self):
        """Build cumulative positions DataFrame."""
        if self.transactions is None or self.transactions.empty:
            return pd.DataFrame()

        records = []
        for _, tx in self.transactions.iterrows():
            ticker = tx['Ticker']
            traded_date = tx['Traded']
            amount = tx['Trade_Size_USD']

            # Determine direction
            if tx['Transaction'] in ['Purchase', 'Buy']:
                sign = 1
            elif tx['Transaction'] in ['Sale', 'Sell', 'Sale (Full)', 'Sale (Partial)']:
                sign = -1
            else:
                continue

            records.append({
                'Date': traded_date,
                'Ticker': ticker,
                'Amount': sign * amount,
                'Filed': tx['Filed'],
                'Trade_Size_USD': amount
            })

        if not records:
            return pd.DataFrame()

        return pd.DataFrame(records).sort_values('Date').reset_index(drop=True)

    def get_position(self, as_of_date, date_type='Date'):
        """Get portfolio positions as of a specific date (in dollar amounts)."""
        if self.positions_df.empty:
            return {}

        as_of = pd.to_datetime(as_of_date)
        df = self.positions_df[self.positions_df[date_type] <= as_of]

        if df.empty:
            return {}

        positions = df.groupby('Ticker')['Amount'].sum().to_dict()
        # Only keep positive positions
        return {k: v for k, v in positions.items() if v > 0}


    def get_portfolio_composition(self, as_of_date, prices_df):
        """Get detailed portfolio composition with current market values.

        Args:
            as_of_date: Date to get composition for
            prices_df: DataFrame of prices from fetch_prices()

        Returns:
            DataFrame with columns: Ticker, Shares, Price, Value, Weight
        """
        as_of = pd.to_datetime(as_of_date)

        # Get cumulative positions in dollars
        dollar_positions = self.get_position(as_of)

        if not dollar_positions:
            print(f"No positions found for {self.name} as of {as_of_date}")
            return pd.DataFrame()

        records = []
        for ticker, dollar_amount in dollar_positions.items():
            # Get price on the as_of date
            price = get_price_on_date(prices_df, ticker, as_of)

            if price and price > 0:
                shares = dollar_amount / price
                current_value = shares * price
                records.append({
                    'Ticker': ticker,
                    'Cost_Basis_USD': dollar_amount,
                    'Shares': shares,
                    'Price': price,
                    'Value': current_value
                })

        if not records:
            return pd.DataFrame()

        df = pd.DataFrame(records)
        total_value = df['Value'].sum()
        df['Weight'] = (df['Value'] / total_value * 100).round(2)
        df = df.sort_values('Value', ascending=False).reset_index(drop=True)

        # Add summary info
        print(f"\n{'='*60}")
        print(f"Portfolio Composition for {self.name}")
        print(f"As of: {as_of_date}")
        print(f"{'='*60}")
        print(f"Total Value: ${total_value:,.2f}")
        print(f"Number of Positions: {len(df)}")
        print(f"{'='*60}\n")

        return df




In [21]:
def fetch_prices(tickers: list, start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE):
    """Fetch historical prices for all tickers."""
    print(f"Fetching prices for {len(tickers)} tickers...")

    # Add buffer for date lookups
    start_dt = pd.to_datetime(start_date) - timedelta(days=30)
    end_dt = pd.to_datetime(end_date) + timedelta(days=5)

    all_prices = {}
    failed_tickers = []

    for i, ticker in enumerate(tickers):
        try:
            data = yf.download(ticker, start=start_dt, end=end_dt, progress=False)
            if not data.empty:
                # Handle potential multi-level columns from yfinance
                close_col = data['Close']
                if isinstance(close_col, pd.DataFrame):
                    # Multi-level columns - flatten
                    close_col = close_col.iloc[:, 0]
                # Ensure we have a Series with float values
                all_prices[ticker] = close_col.astype(float)
            else:
                failed_tickers.append(ticker)
        except Exception as e:
            failed_tickers.append(ticker)

        if (i + 1) % 50 == 0:
            print(f"  Fetched {i+1}/{len(tickers)} tickers")
            time.sleep(1)

    if failed_tickers:
        print(f"Failed to fetch: {len(failed_tickers)} tickers")

    print(f"Successfully fetched prices for {len(all_prices)} tickers")

    prices_df = pd.DataFrame(all_prices)
    prices_df.index = pd.to_datetime(prices_df.index)

    return prices_df, failed_tickers


In [22]:
def get_price_on_date(prices_df, ticker, date, lookback_days=5):
    """Get close price for a ticker on a date (with lookback for non-trading days)."""
    date = pd.to_datetime(date)

    if ticker not in prices_df.columns:
        return None

    ticker_prices = prices_df[ticker].dropna()
    # Try exact date first
    if date in ticker_prices.index:
        return ticker_prices.loc[date]

    # Look back up to lookback_days
    for i in range(1, lookback_days + 1):
        check_date = date - timedelta(days=i)
        if check_date in ticker_prices.index:
            return ticker_prices.loc[check_date]
    return None

## Copy-cat portfolio

In [23]:
class CopycatPortfolio:
    """Simulates a copy-cat portfolio following a legislator's trades.

    Key Logic:
    - Start with INITIAL_CAPITAL as cash
    - Initialize with existing positions from get_position(start_date)
    - Execute trades on Filed date using Filed date prices
    - Shares calculated as: Trade_Size_USD / Traded_date_price
    - Daily portfolio value = cash + sum(shares * current_price)
    """

    def __init__(self, congressman, prices_df):
        self.congressman = congressman
        self.prices_df = prices_df
        self.holdings = {}  # {ticker: shares}
        self.cash = INITIAL_CAPITAL
        self.history = []
        self.snapshots = {}  # {date_str: holdings_dict}

    def simulate(self, start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE):
        """Run the day-by-day simulation."""
        start_dt = pd.to_datetime(start_date)
        end_dt = pd.to_datetime(end_date)

        # Reset state
        self.holdings = {}
        self.cash = INITIAL_CAPITAL

        # Initialize with starting positions from before simulation start
        initial_positions = self.congressman.get_position(start_dt)
        if initial_positions:
            print(f"    Initial positions: {len(initial_positions)} tickers")
            for ticker, dollar_amount in initial_positions.items():
                price = get_price_on_date(self.prices_df, ticker, start_dt)
                if price is not None and price > 0:
                    shares = dollar_amount / price
                    self.holdings[ticker] = shares
                    # Don't reduce cash - we're copying existing positions, not buying them

        # Check if there are any transactions
        if self.congressman.positions_df.empty:
            print(f"    No new transactions to simulate")
            # Still generate returns based on initial holdings
            return self._generate_daily_values(start_dt, end_dt)

        # Get transactions within simulation period (by Filed date)
        txs = self.congressman.positions_df.copy()
        txs['Filed'] = pd.to_datetime(txs['Filed'])
        txs = txs[(txs['Filed'] >= start_dt) & (txs['Filed'] <= end_dt)]

        if txs.empty:
            print(f"    No transactions in date range")
            return self._generate_daily_values(start_dt, end_dt)

        print(f"    Transactions in range: {len(txs)}")

        # Prepare transactions grouped by Filed date
        # Adjust weekend Filed dates to next business day (Monday)
        def adjust_to_next_business_day(d):
            d = pd.to_datetime(d)
            if d.weekday() == 5:  # Saturday -> Monday
                return (d + timedelta(days=2)).date()
            elif d.weekday() == 6:  # Sunday -> Monday
                return (d + timedelta(days=1)).date()
            return d.date()

        txs['Filed_date'] = txs['Filed'].apply(adjust_to_next_business_day)
        trades_by_date = txs.groupby('Filed_date')

        # Generate daily values with trade execution
        date_range = pd.date_range(start=start_dt, end=end_dt, freq='B')  # Business days

        records = []
        initial_stock_value = None
        prev_stock_value = None

        for date in date_range:
            date_key = date.date()

            # Check if there are trades to execute on this date
            if date_key in trades_by_date.groups:
                day_trades = trades_by_date.get_group(date_key)
                self._execute_trades(day_trades, date)

            # Calculate stock holdings value
            stock_value = self._calculate_stock_holdings_value(date)

            # Cash invested = INITIAL_CAPITAL - current_cash
            cash_invested = INITIAL_CAPITAL - self.cash

            # Track initial stock value for cumulative return
            if initial_stock_value is None:
                initial_stock_value = stock_value

            # Cumulative return = (stock_value - initial_stock_value) / cash_invested
            if cash_invested > 0:
                cumulative_return = (stock_value - initial_stock_value) / cash_invested
            else:
                cumulative_return = 0

            # Log return (for plotting)
            if prev_stock_value is not None and prev_stock_value > 0 and stock_value > 0:
                log_return = np.log(stock_value / prev_stock_value)
            else:
                log_return = 0

            records.append({
                'Date': date,
                'stock_value': stock_value,
                'cash': self.cash,
                'cash_invested': cash_invested,
                'portfolio_value': stock_value + self.cash,
                'cumulative_return': cumulative_return,
                'cumulative_return_pct': cumulative_return * 100,
                'log_return': log_return
            })

            prev_stock_value = stock_value

            # Capture snapshots
            date_str = date.strftime('%Y-%m-%d')
            if date_str in SNAPSHOT_DATES:
                self.snapshots[date_str] = self._get_current_holdings_in_dollars(date)

        df = pd.DataFrame(records)

        if not df.empty:
            # Cumulative log return (sum of daily log returns)
            df['cumulative_log_return'] = df['log_return'].cumsum()
        else:
            print(f"    WARNING: No records generated!")

        self.history = df
        return df

    def _generate_daily_values(self, start_dt, end_dt):
        """Generate daily portfolio values for portfolios with no new trades (uses initial holdings)."""
        date_range = pd.date_range(start=start_dt, end=end_dt, freq='B')

        records = []
        initial_stock_value = None
        prev_stock_value = None

        for date in date_range:
            # Calculate stock holdings value
            stock_value = self._calculate_stock_holdings_value(date)
            cash_invested = INITIAL_CAPITAL - self.cash

            # Track initial stock value
            if initial_stock_value is None:
                initial_stock_value = stock_value

            # Cumulative return = (stock_value - initial_stock_value) / cash_invested
            if cash_invested > 0:
                cumulative_return = (stock_value - initial_stock_value) / cash_invested
            else:
                cumulative_return = 0

            # Log return (for plotting)
            if prev_stock_value is not None and prev_stock_value > 0 and stock_value > 0:
                log_return = np.log(stock_value / prev_stock_value)
            else:
                log_return = 0

            records.append({
                'Date': date,
                'stock_value': stock_value,
                'cash': self.cash,
                'cash_invested': cash_invested,
                'portfolio_value': stock_value + self.cash,
                'cumulative_return': cumulative_return,
                'cumulative_return_pct': cumulative_return * 100,
                'log_return': log_return
            })

            prev_stock_value = stock_value

            # Capture snapshots
            date_str = date.strftime('%Y-%m-%d')
            if date_str in SNAPSHOT_DATES:
                self.snapshots[date_str] = self._get_current_holdings_in_dollars(date)

        df = pd.DataFrame(records)

        if not df.empty:
            # Cumulative log return (sum of daily log returns)
            df['cumulative_log_return'] = df['log_return'].cumsum()

        self.history = df
        return df

    def _execute_trades(self, day_trades, current_date):
        """Execute all trades for a given day."""
        for _, tx in day_trades.iterrows():
            ticker = tx['Ticker']
            traded_date = tx['Date']  # Traded date
            trade_size_usd = tx['Trade_Size_USD']
            is_buy = tx['Amount'] > 0

            # Calculate shares using Traded date price
            traded_price = get_price_on_date(self.prices_df, ticker, traded_date)

            # Execute at current (Filed) date price
            filed_price = get_price_on_date(self.prices_df, ticker, current_date)

            if traded_price is None or filed_price is None or traded_price <= 0 or filed_price <= 0:
                continue

            # Shares = Trade_Size_USD / Traded_date_price
            shares = trade_size_usd / traded_price

            if is_buy:
                # Buy shares at Filed price
                cost = shares * filed_price
                self.holdings[ticker] = self.holdings.get(ticker, 0) + shares
                self.cash -= cost
            else:
                # Sell shares at Filed price
                if ticker in self.holdings:
                    shares_to_sell = min(shares, self.holdings[ticker])
                    self.holdings[ticker] -= shares_to_sell
                    self.cash += shares_to_sell * filed_price

                    if self.holdings[ticker] <= 0.0001:
                        del self.holdings[ticker]

    def _calculate_portfolio_value(self, date):
        """Calculate total portfolio value on a given date."""
        portfolio_value = self.cash

        for ticker, shares in self.holdings.items():
            price = get_price_on_date(self.prices_df, ticker, date)
            if price is not None and price > 0:
                portfolio_value += shares * price

        return portfolio_value

    def _calculate_stock_holdings_value(self, date):
        """Calculate total value of stock holdings only (excluding cash)."""
        stock_value = 0

        for ticker, shares in self.holdings.items():
            price = get_price_on_date(self.prices_df, ticker, date)
            if price is not None and price > 0:
                stock_value += shares * price

        return stock_value

    def _get_current_holdings_in_dollars(self, date):
        """Get current holdings valued in dollars."""
        holdings = {}
        for ticker, shares in self.holdings.items():
            price = get_price_on_date(self.prices_df, ticker, date)
            if price and price > 0:
                holdings[ticker] = shares * price
        return holdings

    def get_portfolio_breakdown(self, as_of_date=None):
        """Get detailed portfolio breakdown including cash at a specific date.

        Args:
            as_of_date: Optional date to check. If None, uses current state.
                        Note: For historical dates, you must run simulate() first.

        Returns:
            DataFrame with all positions including cash, with columns:
            Asset, Shares, Price, Value, Weight
        """
        if as_of_date:
            as_of = pd.to_datetime(as_of_date)
        else:
            as_of = None

        records = []
        total_stock_value = 0

        # Add stock holdings
        for ticker, shares in self.holdings.items():
            if as_of:
                price = get_price_on_date(self.prices_df, ticker, as_of)
            else:
                # Use most recent price
                if ticker in self.prices_df.columns:
                    price = self.prices_df[ticker].dropna().iloc[-1]
                else:
                    price = None

            if price and price > 0:
                value = shares * price
                total_stock_value += value
                records.append({
                    'Asset': ticker,
                    'Type': 'Stock',
                    'Shares': shares,
                    'Price': price,
                    'Value': value
                })

        # Add cash
        records.append({
            'Asset': 'CASH',
            'Type': 'Cash',
            'Shares': None,
            'Price': 1.0,
            'Value': self.cash
        })

        df = pd.DataFrame(records)
        total_value = df['Value'].sum()
        df['Weight'] = (df['Value'] / total_value * 100).round(2)
        df = df.sort_values('Value', ascending=False).reset_index(drop=True)

        # Print summary
        print(f"\n{'='*70}")
        print(f"Portfolio Breakdown for {self.congressman.name}")
        if as_of_date:
            print(f"As of: {as_of_date}")
        print(f"{'='*70}")
        print(f"Total Portfolio Value: ${total_value:,.2f}")
        print(f"  - Stock Holdings:    ${total_stock_value:,.2f} ({total_stock_value/total_value*100:.1f}%)")
        print(f"  - Cash:              ${self.cash:,.2f} ({self.cash/total_value*100:.1f}%)")
        print(f"Number of Positions:   {len(self.holdings)}")
        print(f"{'='*70}\n")

        return df


In [24]:
def get_spy_returns(start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE):
    """Get SPY benchmark returns."""
    spy = yf.download('SPY', start=start_date, end=end_date, progress=False)

    df = pd.DataFrame({
        'Date': spy.index,
        'Close': spy['Close'].values.flatten()
    })

    df['daily_return'] = df['Close'].pct_change()
    df['cumulative_return'] = (1 + df['daily_return'].fillna(0)).cumprod() - 1
    df['cumulative_return_pct'] = df['cumulative_return'] * 100

    # Log returns
    df['log_return'] = np.log(1 + df['daily_return']).replace([np.inf, -np.inf], 0).fillna(0)
    df['cumulative_log_return'] = df['log_return'].cumsum()

    return df


In [47]:
congressmen = []
congressmen_by_name = {}
all_tickers = set()

for _, row in lawmakers.iterrows():
    c = Congressman_df(
        name=row['name'], party=row['party'],
        chamber=row['chamber'], state=row['state'],
        bioguide=row['bioguide'], trades_df=raw_df,
    )
    congressmen.append(c)
    congressmen_by_name[c.name] = c
    all_tickers.update(c.tickers)

print(f"  {len(congressmen)} legislators, {len(all_tickers)} unique tickers")


  20 legislators, 1302 unique tickers


In [48]:
all_tickers.add('SPY')
prices_df, failed_tickers = fetch_prices(list(all_tickers), 
                                        start_date=CONGRESS_START_DATE,
                                        end_date=BACKTEST_END_DATE)

Fetching prices for 1302 tickers...



1 Failed download:
['ALOG']: YFPricesMissingError('possibly delisted; no price data found  (1d 2018-12-04 00:00:00 -> 2026-01-05 00:00:00)')

1 Failed download:
['TMK']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['ARGO']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['PPBI']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['WMGI']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['EBSB']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['GCGMF']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['PETQ']: YFTzMissingError('possibly delisted; no timezone found')


  Fetched 50/1302 tickers



1 Failed download:
['DRQ']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['MDSO']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['ABB']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['BHI']: YFPricesMissingError('possibly delisted; no price data found  (1d 2018-12-04 00:00:00 -> 2026-01-05 00:00:00)')

1 Failed download:
['LHCG']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['CHNG']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['SDC']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['AGN']: YFTzMissingError('possibly delisted; no timezone found')


  Fetched 100/1302 tickers


...

  Fetched 1250/1302 tickers



1 Failed download:
['SQ']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['VBTX']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['BECN']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['ADSW']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['HDS']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['FDC']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['FNSXX']: YFPricesMissingError('possibly delisted; no price data found  (1d 2018-12-04 00:00:00 -> 2026-01-05 00:00:00)')

1 Failed download:
['ERI']: YFTzMissingError('possibly delisted; no timezone found')

1 Failed download:
['PFPT']: YFTzMissingError('possibly delisted; no timezone found')


  Fetched 1300/1302 tickers



1 Failed download:
['TPCO']: YFTzMissingError('possibly delisted; no timezone found')


Failed to fetch: 231 tickers
Successfully fetched prices for 1071 tickers


In [49]:
spy_returns = get_spy_returns()

In [51]:
portfolios = {}
copycat_objects = {}

for congressman in congressmen:
    if congressman.transactions is None:
        continue

    print(f"  Simulating: {congressman.name}")
    copycat = CopycatPortfolio(congressman, prices_df)
    result = copycat.simulate()

    if result is not None and len(result) > 0:
        portfolios[congressman.name] = result
        copycat_objects[congressman.name] = copycat

  Simulating: Josh Gottheimer
    Initial positions: 70 tickers
    Transactions in range: 2506
  Simulating: Nancy Pelosi
    Initial positions: 1 tickers
    Transactions in range: 44
  Simulating: Kevin Hern
    Initial positions: 1 tickers
    Transactions in range: 659
  Simulating: Mark Green
    Transactions in range: 618
  Simulating: Bradley S. Schneider
    Initial positions: 5 tickers
    Transactions in range: 50
  Simulating: Virginia Foxx
    Initial positions: 14 tickers
    Transactions in range: 610
  Simulating: Kim Schrier
    Transactions in range: 41
  Simulating: Mikie Sherrill
    Transactions in range: 292
  Simulating: Daniel Meuser
    Transactions in range: 59
  Simulating: Susie Lee
    Transactions in range: 1257
  Simulating: John W. Rose
    Transactions in range: 9
  Simulating: Brian Mast
    Initial positions: 2 tickers
    Transactions in range: 83
  Simulating: Carol Devine Miller
    Transactions in range: 103
  Simulating: Michael C. Burgess
    Tr

## Visualization

In [52]:
mapping = {
    'AA': 'Materials', 'AAGIY': 'Financials', 'AAIGF': 'Financials', 'AAL': 'Industrials', 'AAP': 'Consumer Discretionary',
    'AAPL': 'Technology', 'AB': 'Financials', 'ABBV': 'Healthcare', 'ABCB': 'Financials', 'ABEV': 'Consumer Staples',
    'ABG': 'Consumer Discretionary', 'ABNB': 'Consumer Discretionary', 'ABMD': 'Healthcare', 'ABYIX': 'Fund',
    'ACHC': 'Healthcare', 'ACI': 'Consumer Staples', 'ACIW': 'Technology', 'ACM': 'Industrials', 'ACN': 'Technology',
    'ADBE': 'Technology', 'ADC': 'Real Estate', 'ADDYY': 'Financials', 'ADI': 'Technology', 'ADM': 'Materials',
    'ADP': 'Technology', 'ADSK': 'Technology', 'ADYEY': 'Technology', 'AEE': 'Utilities', 'AEG': 'Financials',
    'AEIS': 'Industrials', 'AEP': 'Utilities', 'AES': 'Utilities', 'AFL': 'Financials', 'AFRM': 'Financials',
    'AGAE': 'Communication Services', 'AGCO': 'Industrials', 'AGIO': 'Healthcare', 'AGX': 'Industrials', 'AHCO': 'Healthcare',
    'AHKSY': 'Industrials', 'AHT': 'Real Estate', 'AI': 'Technology', 'AIG': 'Financials', 'AIO': 'Financials',
    'AIQUY': 'Materials', 'AIR': 'Industrials', 'AJG': 'Financials', 'AKAM': 'Technology', 'ALB': 'Materials',
    'ALC': 'Healthcare', 'ALFVY': 'Industrials', 'ALG': 'Industrials', 'ALGM': 'Technology', 'ALGN': 'Healthcare',
    'ALGT': 'Industrials', 'ALIZY': 'Financials', 'ALK': 'Industrials', 'ALL': 'Financials', 'ALLY.A': 'Financials',
    'ALNY': 'Healthcare', 'AM': 'Energy', 'AMADY': 'Technology', 'AMAT': 'Technology', 'AMC': 'Communication Services',
    'AMD': 'Technology', 'AME': 'Industrials', 'AMGN': 'Healthcare', 'AMLP': 'ETF', 'AMP': 'Financials',
    'AMRC': 'Industrials', 'AMRX': 'Healthcare', 'AMSF': 'Financials', 'AMT': 'Real Estate', 'AMTD': 'Financials',
    'AMTX': 'Materials', 'AMWD': 'Industrials', 'AMZA': 'ETF', 'AMZN': 'Consumer Discretionary', 'ANET': 'Technology',
    'AON': 'Financials', 'AORT': 'Healthcare', 'AOS': 'Industrials', 'APA': 'Energy', 'APD': 'Materials',
    'APH': 'Technology', 'APNHY': 'Healthcare', 'APO': 'Financials', 'APP': 'Communication Services', 'APPF': 'Technology',
    'APU': 'Utilities', 'AQN': 'Utilities', 'AQUA': 'Utilities', 'ARCB': 'Industrials', 'ARCC': 'Financials', 'ARE': 'Real Estate',
    'ARKK': 'ETF', 'ARLP': 'Energy', 'ARMK': 'Consumer Discretionary', 'AROC': 'Energy', 'ARQT': 'Healthcare',
    'ASAZY': 'Industrials', 'ASC': 'Industrials', 'ASIX': 'Materials', 'ASML': 'Technology', 'ASXC': 'Materials',
    'ATKR': 'Industrials', 'ATLKY': 'Industrials', 'ATOAX': 'ETF', 'ATR': 'Healthcare', 'ATRC': 'Healthcare', 'AUY': 'Materials',
    'AVB': 'Real Estate', 'AVGO': 'Technology', 'AVNT': 'Materials', 'AVT': 'Industrials', 'AVTR': 'Healthcare', 'AVY': 'Materials',
    'AWK': 'Utilities', 'AXHE': 'Technology', 'AXP': 'Financials', 'AXS': 'Financials', 'AYR': 'Industrials', 'AZEK': 'Materials',
    'AZN': 'Healthcare', 'AZO': 'Consumer Discretionary', 'AZSEY': 'Financials', 'BAMXY': 'Financials', 'BECN': 'Industrials',
    'BERY': 'Materials', 'BGFV': 'Consumer Discretionary', 'BGNE': 'Healthcare', 'BHI': 'Industrials', 'BKEP': 'Energy',
    'BKI': 'Financials', 'BLL': 'Materials', 'BLUE': 'Consumer Discretionary', 'BPL': 'Energy', 'BPMP': 'Financials',
    'BRK.B': 'Financials', 'BRKS': 'Technology', 'CAA': 'Consumer Discretionary', 'CACI': 'Technology', 'CALD': 'Industrials',
    'CATM': 'Technology', 'CBM': 'Materials', 'CBS': 'Communication Services', 'CCMP': 'Materials', 'CCT': 'Real Estate',
    'CCXI': 'Healthcare', 'CCXX': 'Materials', 'CDK': 'Technology', 'CEB': 'Technology', 'CEQP': 'Energy', 'CERN': 'Healthcare',
    'CHL': 'Materials', 'CHNG': 'Financials', 'CHUY': 'Consumer Discretionary', 'CHX': 'Financials', 'CINR': 'Industrials',
    'CLNC': 'Healthcare', 'CLR': 'Energy', 'CMD': 'Materials', 'CNXM': 'Technology', 'CONE': 'Communication Services',
    'COT': 'Energy', 'COTV': 'Energy', 'CREE': 'Technology', 'CRY': 'Healthcare', 'CTL': 'Communication Services',
    'CTLT': 'Healthcare', 'CTRA': 'Consumer Discretionary', 'CTRM': 'Energy', 'CTXS': 'Technology', 'CVET': 'Healthcare',
    'CWEN.A': 'Utilities', 'CWST': 'Industrials', 'DAIUF': 'Financials', 'DANOY': 'Healthcare', 'DASTY': 'Financials',
    'DBRG': 'Financials', 'DBSDY': 'Financials', 'DCI': 'Industrials', 'DCO': 'Energy', 'DCP': 'Energy', 'DE': 'Industrials',
    'DFKCY': 'Financials', 'DFS': 'Financials', 'DG': 'Consumer Discretionary', 'DHI': 'Consumer Discretionary',
    'DIAL': 'Consumer Discretionary', 'DIFTY': 'Technology', 'DIN': 'Consumer Discretionary', 'DISCA': 'Communication Services',
    'DLPH': 'Industrials', 'DNB': 'Financials', 'DNHBY': 'Financials', 'DNKN': 'Consumer Discretionary', 'DNTUY': 'Financials',
    'DORM': 'Consumer Discretionary', 'DOV': 'Industrials', 'DOW': 'Materials', 'DOX': 'Technology', 'DPLO': 'Financials',
    'DRE': 'Real Estate', 'DRQ': 'Healthcare', 'DSCSY': 'Financials', 'DSDVY': 'Financials', 'DSEY': 'Consumer Discretionary',
    'DSGX': 'Financials', 'DTE': 'Energy', 'DTM': 'Materials', 'DUK': 'Utilities', 'DUKH': 'Utilities', 'DUSA': 'Financials',
    'DVN': 'Energy', 'EADSY': 'Financials', 'EBS': 'Financials', 'EBSB': 'Financials', 'ECOL': 'Materials', 'EDR': 'Energy',
    'EFA': 'ETF', 'EFC': 'Financials', 'EHC': 'Healthcare', 'ELAN': 'Healthcare', 'EMXC': 'ETF', 'ENB': 'Energy',
    'ENBL': 'Technology', 'ENLAY': 'Financials', 'ENLC': 'Energy', 'ENR': 'Energy', 'ENTG': 'Technology', 'ENV': 'Energy',
    'EOG': 'Energy', 'EPAC': 'Financials', 'EPD': 'Energy', 'EPOKY': 'Financials', 'ERI': 'Technology', 'ERJ': 'Industrials',
    'ESGC': 'ETF', 'ESI': 'Healthcare', 'ESL': 'Financials', 'ESLOY': 'Financials', 'ESRX': 'Healthcare', 'ESTC': 'Technology',
    'ET': 'Utilities', 'ETR': 'Utilities', 'ETRN': 'Industrials', 'ETV': 'Industrials', 'EW': 'Healthcare', 'EWBC': 'Financials',
    'EXAS': 'Healthcare', 'EXC': 'Utilities', 'EXLS': 'Technology', 'EXPD': 'Industrials', 'EXPE': 'Consumer Discretionary',
    'EYE': 'Healthcare', 'FAF': 'Financials', 'FANUF': 'Industrials', 'FANUY': 'Industrials', 'FAS': 'Financials', 'FAST': 'Consumer Discretionary',
    'FCX': 'Materials', 'FDC': 'Financials', 'FDEV': 'Technology', 'FDIS': 'ETF', 'FDRR': 'Financials', 'FDS': 'Technology',
    'FDX': 'Industrials', 'FE': 'Utilities', 'FET': 'Technology', 'FEYE': 'Technology', 'FF': 'Energy', 'FHB': 'Financials',
    'FHLC': 'Financials', 'FHN': 'Financials', 'FHYS': 'Financials', 'FI': 'Financials', 'FICO': 'Technology', 'FIVE': 'Consumer Discretionary',
    'FLIR': 'Technology', 'FLL': 'Energy', 'FLNG': 'Energy', 'FLO': 'Consumer Discretionary', 'FLT': 'Industrials',
    'FLYW': 'Industrials', 'FMAT': 'Materials', 'FMC': 'Materials', 'FMS': 'Industrials', 'FMX': 'Materials', 'FNA': 'Financials',
    'FND': 'Consumer Discretionary', 'FNSXX': 'ETF', 'FNV': 'Materials', 'FOUR': 'Financials', 'FOXF': 'Communication Services',
    'FQAL': 'ETF', 'FRC': 'Financials', 'FSK': 'Energy', 'FSKR': 'Energy', 'FSLR': 'Technology', 'FSMDX': 'ETF', 'FSP': 'Financials',
    'FTEC': 'ETF', 'FTK': 'Industrials', 'FTSM': 'Financials', 'FUPBY': 'Financials', 'FVRR': 'Technology', 'FWRG': 'Financials',
    'GBCI': 'Financials', 'GBOOY': 'Financials', 'GCGMF': 'Financials', 'GD': 'Industrials', 'GDDY': 'Technology', 'GDEN': 'Energy',
    'GE': 'Industrials', 'GEL': 'Energy', 'GFL': 'Industrials', 'GGT': 'Materials', 'GH': 'Healthcare', 'GLD': 'ETF',
    'GLIBA': 'Healthcare', 'GLOB': 'Consumer Discretionary', 'GLOP': 'Energy', 'GLP': 'Real Estate', 'GLW': 'Technology',
    'GMAB': 'Healthcare', 'GME': 'Consumer Discretionary', 'GMED': 'Healthcare', 'GMLP': 'Energy', 'GMXAY': 'Financials',
    'GO': 'Technology', 'GOGL': 'Communication Services', 'GPK': 'Materials', 'GPN': 'Technology', 'GPP': 'Energy', 'GRUB': 'Consumer Discretionary',
    'GSK': 'Healthcare', 'GT': 'Industrials', 'GTES': 'Energy', 'GTLS': 'Industrials', 'GTX': 'Industrials', 'GVDNY': 'Financials',
    'GWW': 'Industrials', 'GXO': 'Industrials', 'HACK': 'ETF', 'HAE': 'Healthcare', 'HAIN': 'Consumer Staples', 'HAL': 'Energy',
    'HALO': 'Healthcare', 'HAS': 'Consumer Discretionary', 'HASI': 'Utilities', 'HBAN': 'Financials', 'HCP': 'Real Estate',
    'HCRB': 'Financials', 'HDB': 'Financials', 'HDS': 'Industrials', 'HEI': 'Consumer Discretionary', 'HEI.A': 'Consumer Discretionary',
    'HELE': 'Industrials', 'HES': 'Energy', 'HESAY': 'Energy', 'HESM': 'Energy', 'HFC': 'Energy', 'HHC': 'Financials',
    'HIBB': 'Consumer Discretionary', 'HIG': 'Financials', 'HKXCY': 'Financials', 'HLI': 'Financials', 'HLIO': 'Healthcare',
    'HLMN': 'Healthcare', 'HLN': 'Consumer Discretionary', 'HLT': 'Consumer Discretionary', 'HMN': 'Healthcare', 'HNDL': 'ETF',
    'HOCPY': 'Energy', 'HOLX': 'Healthcare', 'HPP': 'Real Estate', 'HPQ': 'Technology', 'HPT': 'Real Estate', 'HQY': 'Technology',
    'HRB': 'Consumer Discretionary', 'HRC': 'Materials', 'HRI': 'Consumer Discretionary', 'HRL': 'Consumer Staples', 'HRS': 'Industrials',
    'HSBC': 'Financials', 'HSHCY': 'Financials', 'HSIC': 'Healthcare', 'HST': 'Real Estate', 'HSY': 'Consumer Staples', 'HTGC': 'Financials',
    'HTLD': 'Industrials', 'HUBB': 'Industrials', 'HUBS': 'Technology', 'HUM': 'Healthcare', 'HUN': 'Materials', 'HXL': 'Materials',
    'HZN': 'Industrials', 'IAA': 'Industrials', 'IART': 'Healthcare', 'IAU': 'ETF', 'IBDRY': 'Financials', 'IBKC': 'Financials',
    'IBKR': 'Financials', 'IBN': 'Healthcare', 'IBP': 'Consumer Staples', 'ICE': 'Financials', 'ICFI': 'Technology', 'ICLR': 'Healthcare',
    'ICUI': 'Healthcare', 'IDA': 'ETF', 'IFF': 'Materials', 'IFNNY': 'Financials', 'IGSB': 'ETF', 'IGV': 'Technology',
    'IHG': 'Consumer Discretionary', 'IHS': 'Industrials', 'IJR': 'ETF', 'ILMN': 'Healthcare', 'ILPT': 'Real Estate',
    'IMAX': 'Communication Services', 'IMBBY': 'Healthcare', 'IMKTA': 'Consumer Staples', 'INDA': 'ETF', 'INDB': 'Financials',
    'INFO': 'Technology', 'INSM': 'Healthcare', 'INTA': 'Consumer Discretionary', 'INTU': 'Technology', 'IP': 'Materials',
    'IPWR': 'Technology', 'IPXL': 'Healthcare', 'IQV': 'Healthcare', 'IR': 'Materials', 'IRM': 'Industrials', 'IRT': 'Technology',
    'ISRG': 'Healthcare', 'IT': 'Technology', 'ITCI': 'Healthcare', 'ITIP': 'Technology', 'ITT': 'Industrials', 'ITUB': 'Financials',
    'ITW': 'Industrials', 'IVW': 'ETF', 'IVZ': 'Financials', 'IWM': 'ETF', 'IWN': 'ETF', 'IXJ': 'ETF', 'IYZ': 'ETF', 'J': 'Technology',
    'JBL': 'Consumer Discretionary', 'JBT': 'Industrials', 'JCI': 'Industrials', 'JEPI': 'ETF', 'JGCCY': 'Financials', 'JLL': 'Real Estate',
    'JMHLY': 'Healthcare', 'JOE': 'Consumer Discretionary', 'K': 'Consumer Staples', 'KAI': 'Technology', 'KAR': 'Consumer Discretionary',
    'KBCSY': 'Financials', 'KBH': 'Consumer Discretionary', 'KD': 'Consumer Staples', 'KEY': 'Financials', 'KEYS': 'Technology',
    'KHC': 'Consumer Staples', 'KKPNY': 'Financials', 'KKR': 'Financials', 'KLAC': 'Technology', 'KMB': 'Consumer Staples',
    'KMI': 'Energy', 'KMTUY': 'Materials', 'KMX': 'Consumer Discretionary', 'KNOP': 'Energy', 'KOSCF': 'Energy', 'KR': 'Consumer Staples',
    'KS': 'Industrials', 'KUBTY': 'Financials', 'KVUE': 'Communication Services', 'KYCCF': 'Financials', 'KYN': 'Financials',
    'L': 'Consumer Discretionary', 'LAD': 'Financials', 'LAMR': 'Industrials', 'LAND': 'Real Estate', 'LBDAV': 'Financials',
    'LBRDA': 'Financials', 'LBRDK': 'Financials', 'LDNXF': 'Energy', 'LDOS': 'Technology', 'LEA': 'Industrials', 'LEG': 'Consumer Discretionary',
    'LESL': 'Consumer Discretionary', 'LH': 'Healthcare', 'LHCG': 'Healthcare', 'LHX': 'Industrials', 'LIN': 'Materials', 'LITE': 'Technology',
    'LKQ': 'Consumer Discretionary', 'LLDTF': 'Financials', 'LLL': 'Healthcare', 'LLY': 'Healthcare', 'LNEGY': 'Energy', 'LNG': 'Energy',
    'LNT': 'Utilities', 'LOGM': 'Technology', 'LOPE': 'Consumer Discretionary', 'LOW': 'Consumer Discretionary', 'LPLA': 'Materials',
    'LRCX': 'Technology', 'LRLCY': 'Financials', 'LSXMK': 'ETF', 'LTD': 'Consumer Discretionary', 'LTHM': 'Materials', 'LULU': 'Consumer Discretionary',
    'LUMN': 'Communication Services', 'LUMO': 'Technology', 'LUMN': 'Communication Services', 'LUV': 'Industrials', 'LW': 'Industrials',
    'LYB': 'Materials', 'LYG': 'Financials', 'LYV': 'Communication Services', 'LYV': 'Communication Services', 'M': 'Consumer Discretionary',
    'MA': 'Financials', 'MAC': 'Financials', 'MAS': 'Industrials', 'MATX': 'Industrials', 'MBI': 'Financials', 'MBT': 'Financials',
    'MC': 'Financials', 'MCD': 'Consumer Discretionary', 'MCK': 'Healthcare', 'MD': 'Healthcare', 'MDLZ': 'Consumer Staples',
    'MELI': 'Consumer Discretionary', 'META': 'Communication Services', 'MET': 'Financials', 'MGM': 'Consumer Discretionary',
    'MHK': 'Consumer Discretionary', 'MJN': 'Consumer Staples', 'MKC': 'Consumer Staples', 'MKL': 'Financials', 'MKTX': 'Technology',
    'MLM': 'Materials', 'MMC': 'Financials', 'MMM': 'Industrials', 'MNST': 'Consumer Staples', 'MO': 'Consumer Staples',
    'MODN': 'Healthcare', 'MOH': 'Healthcare', 'MON': 'Materials', 'MOS': 'Materials', 'MOV': 'Consumer Discretionary', 'MP': 'Energy',
    'MPW': 'Real Estate', 'MRK': 'Healthcare', 'MRO': 'Energy', 'MSFT': 'Technology', 'MSI': 'Technology', 'MTB': 'Financials',
    'MTCH': 'Communication Services', 'MTD': 'Healthcare', 'MTN': 'Financials', 'MU': 'Technology', 'MUR': 'Energy', 'MXIM': 'Technology',
    'MYGN': 'Healthcare', 'NBL': 'Energy', 'NDAQ': 'Financials', 'NEE': 'Utilities', 'NEP': 'Utilities', 'NET': 'Technology',
    'NFLX': 'Communication Services', 'NKE': 'Consumer Discretionary', 'NLOK': 'Technology', 'NOC': 'Industrials', 'NOV': 'Energy',
    'NOW': 'Technology', 'NP': 'Financials', 'NPTN': 'Technology', 'NRG': 'Utilities', 'NRZ': 'Financials', 'NSC': 'Industrials',
    'NSRGY': 'Consumer Staples', 'NTAP': 'Technology', 'NTES': 'Technology', 'NVDA': 'Technology', 'NVO': 'Healthcare', 'NVR': 'Consumer Discretionary',
    'NWL': 'Consumer Staples', 'NWSA': 'Communication Services', 'NXPI': 'Technology', 'NYCB': 'Financials', 'NYMT': 'Financials',
    'O': 'Real Estate', 'OC': 'Financials', 'ODFL': 'Industrials', 'OGN': 'Energy', 'OKE': 'Energy', 'OMC': 'Consumer Discretionary',
    'ON': 'Healthcare', 'ONB': 'Financials', 'ORCL': 'Technology', 'ORLY': 'Consumer Discretionary', 'OXY': 'Energy', 'PAA': 'Energy',
    'PACD': 'Industrials', 'PANW': 'Technology', 'PAR': 'Consumer Discretionary', 'PAYX': 'Technology', 'PBCT': 'Financials',
    'PBF': 'Energy', 'PCAR': 'Industrials', 'PCLN': 'Consumer Discretionary', 'PDCO': 'Healthcare', 'PEAK': 'Financials',
    'PEG': 'Utilities', 'PEGA': 'Technology', 'PEP': 'Consumer Staples', 'PFE': 'Healthcare', 'PG': 'Consumer Staples',
    'PGR': 'Financials', 'PH': 'Industrials', 'PHG': 'Technology', 'PHM': 'Consumer Discretionary', 'PKG': 'Materials',
    'PKI': 'Healthcare', 'PLD': 'Real Estate', 'PLNT': 'Consumer Discretionary', 'PLUG': 'Energy', 'PM': 'Consumer Staples',
    'PNC': 'Financials', 'PNR': 'Industrials', 'PNW': 'Utilities', 'POOL': 'Consumer Discretionary', 'PPG': 'Materials',
    'PPL': 'Utilities', 'PRGO': 'Healthcare', 'PRU': 'Financials', 'PSA': 'Real Estate', 'PSX': 'Energy', 'PTC': 'Technology',
    'PTON': 'Consumer Discretionary', 'PUBGY': 'Financials', 'PVH': 'Consumer Discretionary', 'PWR': 'Industrials', 'PXD': 'Energy',
    'PYPL': 'Technology', 'QCOM': 'Technology', 'QRTEA': 'Technology', 'QSR': 'Consumer Discretionary', 'R': 'Consumer Discretionary',
    'RACE': 'Consumer Discretionary', 'RCL': 'Consumer Discretionary', 'RE': 'Financials', 'REG': 'Industrials', 'REGN': 'Healthcare',
    'RF': 'Financials', 'RHI': 'Industrials', 'RIG': 'Energy', 'RIO': 'Materials', 'RIVN': 'Consumer Discretionary', 'RL': 'Consumer Discretionary',
    'ROK': 'Industrials', 'ROP': 'Industrials', 'ROST': 'Consumer Discretionary', 'RPRX': 'Healthcare', 'RPM': 'Materials',
    'RPRX': 'Healthcare', 'RS': 'Technology', 'RSG': 'Industrials', 'RTX': 'Industrials', 'RUN': 'Utilities', 'RY': 'Financials',
    'SBUX': 'Consumer Discretionary', 'SCHW': 'Financials', 'SEE': 'Industrials', 'SHW': 'Materials', 'SIRI': 'Communication Services',
    'SIVB': 'Financials', 'SJM': 'Consumer Staples', 'SLB': 'Energy', 'SLG': 'Real Estate', 'SMG': 'Consumer Discretionary',
    'SNA': 'Industrials', 'SNOW': 'Technology', 'SNPS': 'Technology', 'SO': 'Utilities', 'SPG': 'Real Estate', 'SPGI': 'Financials',
    'SPLK': 'Technology', 'SPOT': 'Technology', 'SPWR': 'Utilities', 'SQ': 'Technology', 'SQM': 'Materials', 'SRCL': 'Industrials',
    'SRE': 'Utilities', 'STAG': 'Real Estate', 'STLD': 'Materials', 'STT': 'Financials', 'STX': 'Technology', 'STZ': 'Consumer Staples',
    'SU': 'Energy', 'SWKS': 'Technology', 'SYK': 'Healthcare', 'SYF': 'Financials', 'SYY': 'Consumer Staples', 'T': 'Communication Services',
    'TAP': 'Consumer Staples', 'TDC': 'Technology', 'TDG': 'Industrials', 'TDY': 'Industrials', 'TECH': 'Technology', 'TEL': 'Technology',
    'TER': 'Healthcare', 'TEX': 'Materials', 'TFX': 'Healthcare', 'TGT': 'Consumer Discretionary', 'TJX': 'Consumer Discretionary',
    'TMUS': 'Communication Services', 'TMO': 'Healthcare', 'TPR': 'Consumer Discretionary', 'TRMB': 'Technology', 'TRN': 'Industrials',
    'TRP': 'Energy', 'TRV': 'Financials', 'TSLA': 'Consumer Discretionary', 'TSM': 'Technology', 'TT': 'Industrials', 'TTD': 'Technology',
    'TTE': 'Energy', 'TTMI': 'Technology', 'TWTR': 'Communication Services', 'TXN': 'Technology', 'TXT': 'Industrials', 'TYL': 'Industrials',
    'UA': 'Consumer Discretionary', 'UAA': 'Consumer Discretionary', 'UAL': 'Industrials', 'UDR': 'Real Estate', 'UHS': 'Healthcare',
    'UHT': 'Real Estate', 'ULTA': 'Consumer Discretionary', 'UNH': 'Healthcare', 'UNM': 'Financials', 'UNP': 'Industrials',
    'UPS': 'Industrials', 'URI': 'Industrials', 'USB': 'Financials', 'V': 'Financials', 'VFC': 'Consumer Discretionary', 'VICI': 'Real Estate',
    'VLO': 'Energy', 'VMC': 'Materials', 'VNO': 'Real Estate', 'VTR': 'Real Estate', 'VZ': 'Communication Services', 'WAB': 'Industrials',
    'WAT': 'Industrials', 'WBA': 'Consumer Staples', 'WDC': 'Technology', 'WEC': 'Utilities', 'WELL': 'Real Estate', 'WES': 'Industrials',
    'WFC': 'Financials', 'WHR': 'Consumer Discretionary', 'WM': 'Industrials', 'WMB': 'Energy', 'WMT': 'Consumer Staples', 'WRB': 'Financials',
    'WRK': 'Industrials', 'WRLD': 'Technology', 'WU': 'Financials', 'WYNN': 'Consumer Discretionary', 'XEL': 'Utilities', 'XOM': 'Energy',
    'XRAY': 'Healthcare', 'XYL': 'Industrials', 'YUM': 'Consumer Discretionary', 'ZBH': 'Healthcare', 'ZBRA': 'Technology',
    'ZION': 'Financials', 'ZM': 'Technology', 'ZS': 'Technology', 'ZTS': 'Healthcare',    'BP': 'Energy',
    'CCI': 'Real Estate',
    'CMCSA': 'Communication Services',
    'DIS': 'Communication Services',
    'TTWO': 'Communication Services',
    'DXCM': 'Healthcare',
    'BEP': 'Utilities',
    'TDOC': 'Healthcare',
    'GS': 'Financials',
    'ALLY': 'Financials',
    'MS': 'Financials',
    'EL': 'Consumer Staples',
    'CYRX': 'Healthcare',
    'COST': 'Consumer Staples',
    'JPM': 'Financials',
    'CDNS': 'Technology',
    'LVMHF': 'Consumer Discretionary',
    'CGNX': 'Technology',
    'NTLA': 'Healthcare',
    'MSCI': 'Financials',
    'USO': 'ETF',
    'ECL': 'Materials',
    'BROS': 'Consumer Discretionary',
    'F': 'Consumer Discretionary',
    'NWN': 'Utilities',
    'WY': 'Financials',
    'COHR': 'Technology',
    'INTC': 'Technology',
    'HD': 'Consumer Discretionary',
    'BX': 'Financials',
    'GILD': 'Healthcare',
    'BLK': 'Financials',
    'BAC': 'Financials',
    'CVS': 'Consumer Staples',
    'CSCO': 'Technology',
    'CRM': 'Technology',
    'CAT': 'Industrials',
    'DGX': 'Healthcare',
    'JNJ': 'Healthcare',
    'CB': 'Financials',
    'C': 'Financials',
    'MDT': 'Healthcare',
    'SAP': 'Technology',
    'VOD': 'Communication Services',
    'POR': 'Utilities',
    'UL': 'Consumer Staples',
    'NEM': 'Materials',
    'MEOH': 'Materials',
    'FLEX': 'Technology',
    'BWA': 'Consumer Discretionary',
    'DD': 'Materials',
    'SWK': 'Industrials',
    'CI': 'Healthcare',
    'D': 'Utilities',
    'FLR': 'Industrials',
    'WWD': 'Consumer Discretionary',
    'CME': 'Financials',
    'MPC': 'Energy',
    'HON': 'Industrials',
    'GOOG': 'Technology',
    'LVMUY': 'Consumer Discretionary',
    'RHHBF': 'Healthcare',
    'DLTR': 'Consumer Discretionary',
    'ABTSTLA': 'Healthcare',
    'BTI': 'Consumer Staples',
    'CVX': 'Energy',
    'EMR': 'Industrials',
    'ABT': 'Healthcare',
    'SHY': 'ETF',
    'VUG': 'ETF',
    'YETI': 'Consumer Discretionary',
    'UBER': 'Technology',
    'SPCE': 'Consumer Discretionary',
    'SNAP': 'Communication Services',
    "LMT": "Aerospace & Defense",
    "RHHBY": "Pharmaceuticals",
    "OLP": "Real Estate / Investment Trust",
    "LZAGY": "Chemicals / Industrial Materials",
    "BEN": "Financial Services / Asset Management",
    "MFC": "Financial Services / Insurance"
}


In [53]:
def plot_summary(portfolio_df, spy_df, legislator_name, INDUSTRY_MAP, snapshots, plottype="", save_path=None):

    # -------------------------
    # SUBPLOTS LAYOUT (4 ROWS, 3 COLS)
    # -------------------------
    fig = make_subplots(
        rows=4, cols=3,
        specs=[
            [{"colspan": 3}, None, None],  # Row 1: Line chart
            [None, None, None],            # Row 2: Empty spacer
            [{"type": "domain"}]*3,        # Row 3: Sunbursts
            [{"type": "domain"}]*3         # Row 4: Sunbursts
        ],
        row_heights=[0.4, 0.05, 0.275, 0.275],
        vertical_spacing=0.05,
        horizontal_spacing=0.03,
        subplot_titles=["Cumulative Returns"] + list(snapshots.keys()) # Limit titles to match available slots
    )

    # -------------------------
    # LINE PLOT
    # -------------------------
    # Portfolio returns
    fig.add_trace(go.Scatter(
        x=portfolio_df['Date'],
        y=portfolio_df['cumulative_return_pct'],
        mode='lines',
        name=f'{legislator_name} Portfolio vs SPY',
        line=dict(width=2)
    ))


    # SPY returns
    fig.add_trace(go.Scatter(
        x=spy_df['Date'],
        y=spy_df['cumulative_return_pct'],
        mode='lines',
        name='SPY',
        line=dict(width=2, dash='dash', color='gray')
    ))


    fig.update_xaxes(title_text="Date",
                      row=1, col=1)
    fig.update_yaxes(
        title_text='Cumulative Return (%)'
,
        row=1, col=1
      )

    fig.update_layout(
        legend=dict(
            orientation="v",      # vertical or "h" if you prefer horizontal
            x=0.02,               # position on x-axis (0=left, 1=right)
            y=0.98,               # position on y-axis (0=bottom, 1=top)
            xanchor="left",      # anchors the legend box
            yanchor="top",
            bgcolor="rgba(255,255,255,0.7)",  # semi-transparent background

        )
    )

    # Use SNAPSHOT_DATES from global scope for subplot titles and iteration
    # Note: SNAPSHOT_DATES is already defined as a list of strings

    # -------------------------
    # SUNBURSTS (rows 3 & 4)
    # -------------------------

    for i, date_str in enumerate(snapshots.keys()): # Iterate only over the first 6 snapshots
        if date_str not in snapshots:
            print(f"Warning: Snapshot for {date_str} not found for {legislator_name}. Skipping.")
            continue
        w = snapshots[date_str]
        df = pd.Series(w).rename("Weight").reset_index().rename(columns={"index": "Ticker"})
        df["Industry"] = df["Ticker"].map(INDUSTRY_MAP)
        df["Industry"] = df["Industry"].fillna("Unknown")
        df = df[df["Weight"] > 0]
        if df.empty:
            continue

        sunburst = px.sunburst(
            df,
            path=["Industry", "Ticker"],
            values="Weight",
            color="Industry"
        )
        sunburst.update_traces(
            textinfo="label+percent parent",
            hovertemplate="<b>%{label}</b><br>%{value:.2%}<extra></extra>"
        )

        # Calculate row/col for sunbursts (row 3 & 4)
        row = (i // 3) + 3  # starts at row 3
        col = (i % 3) + 1
        fig.add_trace(sunburst.data[0], row=row, col=col)

    # -------------------------
    # Sunburst subtitle
    # -------------------------
    fig.add_annotation(
        text="Yearly Weighted Portfolio",
        x=0.5,
        y=0.6,  # centered between line chart and sunbursts
        xref="paper",
        yref="paper",
        showarrow=False,
        font=dict(size=16)
    )

    # -------------------------
    # Layout tweaks
    # -------------------------
    fig.update_layout(
        height=1800,  # taller to fill page
        width=1200,
        title_text=f"{legislator_name}<br>Cumulative {plottype} Portfolio Performance", # Use legislator_name instead of undefined congressman.name
        showlegend=True,
        margin=dict(t=100, l=50, r=50, b=50),
        hovermode="x unified",
        plot_bgcolor="rgba(245,245,245,0.6)",
        paper_bgcolor="white"
    )

    # -------------------------
    # Save figure dynamically
    # -------------------------
    safe_name = re.sub(r'[^0-9a-zA-Z_]', '', legislator_name.replace(" ", "_")) # Use legislator_name
    filename = f"{safe_name}_summary.html"
    if save_path:
      fig.write_html(os.path.join(save_path, filename))

    fig.show()


In [54]:
summary_dir = os.path.join(OUTPUT_DIR, 'summary')
os.makedirs(summary_dir, exist_ok=True)

# Iterate over the portfolios dictionary
for name, portfolio_df in portfolios.items():

    safe_name = name.replace(" ", "_").replace(".", "")
    save_path = os.path.join(summary_dir, f"{safe_name}_cc_summary.html")

    plot_summary(portfolio_df, spy_returns, name, mapping, copycat_objects[name].snapshots, save_path=summary_dir)

## Comparison

In [55]:
def get_last_available_value(series, date):
    """
    Returns the last available value in a Series
    at or before the given date.
    """
    eligible = series.loc[:date]
    if eligible.empty:
        return np.nan
    return eligible.iloc[-1]


snapshot_dates_comp = pd.to_datetime(SNAPSHOT_DATES)

# Prepare SPY series
spy_df = spy_returns.copy()
spy_df['Date'] = pd.to_datetime(spy_df['Date'])
spy_series = spy_df.set_index('Date')['cumulative_return_pct']

rows = {}

for politician, df in portfolios.items():
    df = df.copy()
    df['Date'] = pd.to_datetime(df['Date'])
    portfolio_series = df.set_index('Date')['cumulative_return_pct']

    row = {}

    for date in snapshot_dates_comp:
        portfolio_val = get_last_available_value(portfolio_series, date)
        spy_val = get_last_available_value(spy_series, date)

        if pd.notna(portfolio_val) and pd.notna(spy_val):
            row[date.strftime('%Y-%m-%d')] = portfolio_val - spy_val
        else:
            row[date.strftime('%Y-%m-%d')] = np.nan

    rows[politician] = row

comparison_table = pd.DataFrame.from_dict(rows, orient='index')
comparison_table

2019-01-03  2019-12-31  2020-12-31   2021-12-31  \
Josh Gottheimer                  0.0  157.524656  174.812948   132.015737   
Nancy Pelosi                     0.0  -34.292113   79.252639    25.990368   
Kevin Hern                       0.0   72.863278   68.366301    13.125567   
Mark Green                       0.0  -34.292113   67.443564    61.455335   
Bradley S. Schneider             0.0  -34.292113  -58.910000  -104.562902   
Virginia Foxx                    0.0  104.261119   48.651377    14.322779   
Kim Schrier                      0.0  -34.292113  -58.910000    19.275342   
Mikie Sherrill                   0.0   73.555572   90.493990    82.224235   
Daniel Meuser                    0.0  -34.292113  -58.910000    -3.915750   
Susie Lee                        0.0   81.138296   69.284934    38.293222   
John W. Rose                     0.0  -34.292113  -58.910000  -104.562902   
Brian Mast                       0.0  103.556250  -58.910000  1364.132781   
Carol Devine Miller              0.0  -34.292113   46.373076    27.324535   
Michael C. Burgess               0.0  -34.292113  -58.910000    -4.562902   
Pete Sessions                    0.0  -34.292113  -58.910000   102.717729   
Lois Frankel                     0.0  103.754424   65.849002    43.260661   
Earl Blumenauer                  0.0  128.715159   97.099130    94.014592   
Michael Garcia                   0.0  -34.292113  283.988384   160.449865   
Donald Sternoff Beyer Jr         0.0   66.722288  207.605772   265.680354   
Debbie Dingell                   0.0  130.564132  105.775416   184.720855   

                            2022-12-31   2023-12-31    2024-12-31  \
Josh Gottheimer             103.949864   126.664393 -1.637559e+02   
Nancy Pelosi                  9.249727   -19.700455 -4.148931e+01   
Kevin Hern                   36.505373     8.438070 -2.736849e+01   
Mark Green                  137.736979   312.810596  1.146584e+04   
Bradley S. Schneider        -67.382824  -111.196581 -1.637559e+02   
Virginia Foxx               143.287479    85.532719  4.202491e+01   
Kim Schrier                 -67.382824  -111.196581 -1.637559e+02   
Mikie Sherrill               78.354983    74.644862  6.458163e+01   
Daniel Meuser                 5.892822   -10.800598 -4.368747e+01   
Susie Lee                    47.708498    34.603728  3.110089e+00   
John W. Rose                -67.382824  -111.196581 -1.637559e+02   
Brian Mast                  -67.382824  -111.196581 -1.637559e+02   
Carol Devine Miller          48.898912     6.918823 -3.407100e+01   
Michael C. Burgess           50.315380    -3.452726 -5.983994e+01   
Pete Sessions                74.748700   139.640879  3.436512e+02   
Lois Frankel                 71.274809   107.658997  9.080384e+01   
Earl Blumenauer              48.822394    25.459205 -2.055591e+01   
Michael Garcia               18.874850  -111.196581 -1.637559e+02   
Donald Sternoff Beyer Jr  70126.353289  2333.214860  4.425073e+07   
Debbie Dingell              152.895885    69.540821  6.600574e+01   

                            2025-01-02  
Josh Gottheimer          -1.637559e+02  
Nancy Pelosi             -3.976317e+01  
Kevin Hern               -2.750983e+01  
Mark Green                1.164350e+04  
Bradley S. Schneider     -1.637559e+02  
Virginia Foxx             4.475564e+01  
Kim Schrier              -1.637559e+02  
Mikie Sherrill            6.439281e+01  
Daniel Meuser            -4.431877e+01  
Susie Lee                 3.329365e+00  
John W. Rose             -1.637559e+02  
Brian Mast               -1.637559e+02  
Carol Devine Miller      -3.421807e+01  
Michael C. Burgess       -6.049358e+01  
Pete Sessions             3.454492e+02  
Lois Frankel              9.012522e+01  
Earl Blumenauer          -2.137780e+01  
Michael Garcia           -1.637559e+02  
Donald Sternoff Beyer Jr  4.425073e+07  
Debbie Dingell            6.560459e+01

In [56]:
comparison_table.describe()

2019-01-03  2019-12-31  2020-12-31   2021-12-31    2022-12-31  \
count        20.0   20.000000   20.000000    20.000000     20.000000   
mean          0.0   33.986702   49.631327   120.569975   3544.266932   
std           0.0   72.981684   99.286876   305.677434  15671.947633   
min           0.0  -34.292113  -58.910000  -104.562902    -67.382824   
25%           0.0  -34.292113  -58.910000    14.023476      8.410500   
50%           0.0   16.215087   66.646283    40.776941     48.860653   
75%           0.0  103.605793   92.145275   110.042231     84.753703   
max           0.0  157.524656  283.988384  1364.132781  70126.353289   

        2023-12-31    2024-12-31    2025-01-02  
count    20.000000  2.000000e+01  2.000000e+01  
mean    136.759563  2.213080e+06  2.213089e+06  
std     527.997247  9.894636e+06  9.894634e+06  
min    -111.196581 -1.637559e+02 -1.637559e+02  
25%     -42.574487 -1.637559e+02 -1.637559e+02  
50%      16.948637 -3.071975e+01 -3.086395e+01  
75%      91.064288  6.493766e+01  6.469575e+01  
max    2333.214860  4.425073e+07  4.425073e+07

# Portfolio optimization

In [59]:
def get_risk_free_rate():
    """Fetch 3-month US Treasury Bill rate from FRED via yfinance."""
    try:
        # ^IRX is the 13-week Treasury Bill rate
        tbill = yf.download('^IRX', period='5d', progress=False)
        if not tbill.empty:
            rate = tbill['Close'].iloc[-1].item() / 100  # Convert to decimal
            return rate
    except Exception as e:
        print(f"Could not fetch T-bill rate: {e}")
    # Default fallback
    return 0.045  # 4.5% as fallback


def get_top_n_stocks_at_date(congressmen_list, date, n=20, prices_df=None):

    all_holdings = {}
    as_of = pd.to_datetime(date)

    for congressman in congressmen_list:
        # Use get_position which already calculates net positions
        positions = congressman.get_position(as_of)

        for ticker, net_amount in positions.items():
            if net_amount > 0:  # Only positive net positions
                # Filter: only include if ticker exists in prices_df
                if prices_df is not None:
                    if ticker not in prices_df.columns:
                        continue
                    # Also check if there's actually data for this ticker
                    if prices_df[ticker].dropna().empty:
                        continue

                all_holdings[ticker] = all_holdings.get(ticker, 0) + net_amount

    # Sort by net exposure and return top N
    sorted_stocks = sorted(all_holdings.items(), key=lambda x: x[1], reverse=True)
    return sorted_stocks[:n]


def get_rebalance_dates(start_date, end_date, freq='quarterly'):

    start_dt = pd.to_datetime(start_date)
    end_dt = pd.to_datetime(end_date)

    freq_map = {
        'weekly': 'W-FRI',
        'bi-weekly': '2W-FRI',
        'monthly': 'ME',
        'quarterly': 'QE',
        'annually': 'YE'
    }

    pandas_freq = freq_map.get(freq, 'QE')
    dates = pd.date_range(start=start_dt, end=end_dt, freq=pandas_freq)

    # Ensure start date is included as first rebalance
    if len(dates) == 0 or dates[0] > start_dt:
        dates = pd.DatetimeIndex([start_dt]).append(dates)

    # Adjust to nearest earlier business day if not a business day
    adjusted_dates = []
    for d in dates:
        # If weekend, roll back to Friday
        if d.weekday() == 5:  # Saturday
            d = d - timedelta(days=1)
        elif d.weekday() == 6:  # Sunday
            d = d - timedelta(days=2)
        adjusted_dates.append(d)

    return adjusted_dates



In [60]:
class CustomPortfolio:


    def __init__(self, congressmen_list, prices_df,
                 rebalance_freq='quarterly', n_stocks=20,
                 lookback_months=12, weighting='equal_value'):
        self.congressmen_list = congressmen_list
        self.prices_df = prices_df
        self.rebalance_freq = rebalance_freq
        self.n_stocks = n_stocks
        self.lookback_months = lookback_months
        self.weighting = weighting

        self.holdings = {}  # {ticker: shares}
        self.holdings_history = {}  # {date: holdings_dict}
        self.history = None
        self.rebalance_log = []

    def simulate(self, start_date=CONGRESS_START_DATE, end_date=CONGRESS_END_DATE, debug=False):
        """Run day-by-day simulation with periodic rebalancing."""
        start_dt = pd.to_datetime(start_date)
        end_dt = pd.to_datetime(end_date)

        # Reset state
        self.holdings = {}
        self.holdings_history = {}
        self.rebalance_log = []

        # Get rebalance dates
        rebalance_dates = get_rebalance_dates(start_date, end_date, self.rebalance_freq)
        rebalance_set = set(d.date() for d in rebalance_dates)

        if debug:
            print(f"Rebalance dates: {len(rebalance_dates)}")
            print(f"First 5: {[d.strftime('%Y-%m-%d') for d in rebalance_dates[:5]]}")

        # Generate daily values
        date_range = pd.date_range(start=start_dt, end=end_dt, freq='B')

        records = []
        prev_stock_value = None

        for date in date_range:
            date_key = date.date()

            # Rebalance on rebalance dates
            if date_key in rebalance_set:
                # Amount to invest = previous day's stock value (for continuity)
                # On first rebalance, use INITIAL_CAPITAL
                amount_to_invest = prev_stock_value if prev_stock_value is not None else INITIAL_CAPITAL

                if debug:
                    print(f"REBALANCE {date.strftime('%Y-%m-%d')}: investing ${amount_to_invest:,.0f}")

                self._rebalance(date, amount_to_invest)

            # Calculate stock holdings value
            stock_value = self._calculate_stock_value(date)

            # Store holdings snapshot for this date
            self.holdings_history[date] = dict(self.holdings)

            records.append({
                'Date': date,
                'stock_value': stock_value,
                'n_holdings': len(self.holdings)
            })

            prev_stock_value = stock_value

        # Create DataFrame and calculate returns
        df = pd.DataFrame(records)

        if not df.empty:
            # Daily return = percentage change of stock_value
            df['daily_return'] = df['stock_value'].pct_change().fillna(0)

            # Cumulative return = cumprod of (1 + daily_return) - 1
            df['cumulative_return'] = (1 + df['daily_return']).cumprod() - 1
            df['cumulative_return_pct'] = df['cumulative_return'] * 100

            # Log returns
            df['log_return'] = np.log(1 + df['daily_return']).replace([np.inf, -np.inf], 0).fillna(0)
            df['cumulative_log_return'] = df['log_return'].cumsum()

        self.history = df
        return df

    def _rebalance(self, date, amount_to_invest):
        """Rebalance portfolio: sell all, buy new top N stocks.

        Key: invest exactly amount_to_invest (= prev day's stock value)
        to ensure stock_value continuity across rebalance.
        """
        # Get top N stocks
        top_stocks = get_top_n_stocks_at_date(self.congressmen_list, date, self.n_stocks,  prices_df=self.prices_df)

        if not top_stocks:
            return

        tickers = [t[0] for t in top_stocks]

        # Clear holdings
        self.holdings = {}

        # Get weights
        weights = self._get_weights(tickers, date)

        # Buy new positions
        for ticker, weight in zip(tickers, weights):
            if weight <= 0:
                continue

            price = get_price_on_date(self.prices_df, ticker, date)
            if price is None or price <= 0:
                continue

            dollars = amount_to_invest * weight
            shares = dollars / price
            self.holdings[ticker] = shares

        self.rebalance_log.append({
            'date': date,
            'amount_invested': amount_to_invest,
            'n_stocks': len(self.holdings),
            'tickers': list(self.holdings.keys())
        })

    def _get_weights(self, tickers, date):
        """Calculate portfolio weights based on weighting scheme.
        Only includes tickers that have valid prices in prices_df.
        """
        # First, filter to tickers that have valid prices
        valid_tickers = []
        valid_prices = []

        for t in tickers:
            p = get_price_on_date(self.prices_df, t, date)
            if p is not None and p > 0:
                valid_tickers.append(t)
                valid_prices.append(p)

        n = len(valid_tickers)
        if n == 0:
            return [0] * len(tickers)  # No valid tickers

        if self.weighting == 'equal_share_weight':
            # Equal number of shares - weight proportional to 1/price
            total_price = sum(valid_prices)
            valid_weights = [p / total_price for p in valid_prices]

        elif self.weighting == 'equal_value':
            # Equal dollar value per stock
            valid_weights = [1 / n] * n

        elif self.weighting == 'mean_variance':
            return self._calculate_mean_variance_weights(tickers, date)

        else:
            valid_weights = [1 / n] * n

        # Map back to original ticker list (0 weight for missing tickers)
        weight_map = dict(zip(valid_tickers, valid_weights))
        return [weight_map.get(t, 0) for t in tickers]

    def _calculate_mean_variance_weights(self, tickers, date):
        """Calculate mean-variance optimal weights (minimum variance)."""
        n = len(tickers)

        # Get historical returns
        end_date = pd.to_datetime(date)
        start_date = end_date - timedelta(days=self.lookback_months * 30)

        returns_data = []
        valid_tickers = []

        for ticker in tickers:
            if ticker not in self.prices_df.columns:
                continue

            prices = self.prices_df[ticker].loc[start_date:end_date].dropna()
            if len(prices) < 20:
                continue

            returns = prices.pct_change().dropna()
            if len(returns) > 0:
                returns_data.append(returns)
                valid_tickers.append(ticker)

        if len(valid_tickers) < 2:
            return [1 / n] * n

        # Align returns
        returns_df = pd.DataFrame({t: r for t, r in zip(valid_tickers, returns_data)})
        returns_df = returns_df.dropna()

        if len(returns_df) < 2:
            return [1 / n] * n

        # Covariance matrix
        cov_matrix = returns_df.cov().values
        n_valid = len(valid_tickers)

        # Minimize variance
        def portfolio_variance(w):
            return w @ cov_matrix @ w

        constraints = {'type': 'eq', 'fun': lambda w: np.sum(w) - 1}
        bounds = [(0, 0.25) for _ in range(n_valid)]
        x0 = np.array([1 / n_valid] * n_valid)

        try:
            result = minimize(portfolio_variance, x0, method='SLSQP',
                            bounds=bounds, constraints=constraints)
            optimized = result.x if result.success else x0
        except:
            optimized = x0

        # Map back to original tickers
        ticker_weights = dict(zip(valid_tickers, optimized))
        weights = [ticker_weights.get(t, 0) for t in tickers]

        # Normalize
        total = sum(weights)
        if total > 0:
            weights = [w / total for w in weights]
        else:
            weights = [1 / n] * n

        return weights

    def _calculate_stock_value(self, date):
        """Calculate total value of stock holdings."""
        total = 0
        for ticker, shares in self.holdings.items():
            price = get_price_on_date(self.prices_df, ticker, date)
            if price is not None and price > 0:
                total += shares * price
        return total

    def get_portfolio_composition(self, date=None):

        if date:
            as_of = pd.to_datetime(date)
            # Look up holdings from history for this date
            # Find the closest date in holdings_history that is <= as_of
            available_dates = sorted(self.holdings_history.keys())
            holdings_to_use = {}
            for d in available_dates:
                if d <= as_of:
                    holdings_to_use = self.holdings_history[d]
                else:
                    break
            if not holdings_to_use and available_dates:
                # If date is before first rebalance, use first available
                holdings_to_use = self.holdings_history[available_dates[0]]
        else:
            as_of = None
            holdings_to_use = self.holdings  # Use current holdings

        records = []
        total_stock_value = 0
        missing_tickers = []

        # Add stock holdings
        for ticker, shares in holdings_to_use.items():
            if as_of:
                price = get_price_on_date(self.prices_df, ticker, as_of)
            else:
                if ticker in self.prices_df.columns:
                    prices = self.prices_df[ticker].dropna()
                    price = prices.iloc[-1] if not prices.empty else None
                else:
                    price = None

            if price is not None and price > 0:
                value = shares * price
                total_stock_value += value
                records.append({
                    'Asset': ticker, 'Type': 'Stock',
                    'Shares': shares, 'Price': price, 'Value': value
                })
            else:
                missing_tickers.append(ticker)
                records.append({
                    'Asset': ticker, 'Type': 'Stock',
                    'Shares': shares, 'Price': None, 'Value': 0
                })

        df = pd.DataFrame(records)

        # Calculate weights based on total stock value
        if not df.empty and total_stock_value > 0:
            df['Weight (%)'] = (df['Value'] / total_stock_value * 100).round(2)
        elif not df.empty:
            df['Weight (%)'] = 0

        if not df.empty:
            df = df.sort_values('Value', ascending=False).reset_index(drop=True)

        # Print summary
        date_str = as_of.strftime('%Y-%m-%d') if as_of else 'Current'
        print(f"\n{'='*70}")
        print(f"Portfolio Composition - {date_str}")
        print(f"Weighting: {self.weighting}, Rebalance: {self.rebalance_freq}")
        print(f"{'='*70}")
        print(f"Total Value:         ${total_stock_value:,.2f}")
        print(f"Number of Positions: {len(holdings_to_use)}")
        if missing_tickers:
            print(f"Missing Prices:      {len(missing_tickers)} - {missing_tickers[:5]}")
        print(f"{'='*70}\n")

        return df


## Equal Share Weighted portfolio

In [61]:
equal_share_weight = CustomPortfolio(congressmen, prices_df, weighting='equal_share_weight')
equal_share_weight.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000          20  0.000000e+00           0.000000   
1    2019-01-04  103338.371533          20  3.338372e-02           0.033384   
2    2019-01-07  104716.937406          20  1.334031e-02           0.047169   
3    2019-01-08  106015.324823          20  1.239902e-02           0.060153   
4    2019-01-09  106134.660088          20  1.125642e-03           0.061347   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  228848.470891          20 -1.064992e-02           1.288485   
1562 2024-12-30  226122.268280          20 -1.191270e-02           1.261223   
1563 2024-12-31  226122.268280          20  2.220446e-16           1.261223   
1564 2025-01-01  226122.268280          20  0.000000e+00           1.261223   
1565 2025-01-02  225544.580750          20 -2.554757e-03           1.255446   

      cumulative_return_pct    log_return  cumulative_log_return  
0                  0.000000  0.000000e+00               0.000000  
1                  3.338372  3.283858e-02               0.032839  
2                  4.716937  1.325211e-02               0.046091  
3                  6.015325  1.232278e-02               0.058413  
4                  6.134660  1.125009e-03               0.059538  
...                     ...           ...                    ...  
1561             128.848471 -1.070703e-02               0.827890  
1562             126.122268 -1.198422e-02               0.815906  
1563             126.122268  2.220446e-16               0.815906  
1564             126.122268  0.000000e+00               0.815906  
1565             125.544581 -2.558026e-03               0.813348  

[1566 rows x 8 columns]

## Equal market cap portfolio

In [62]:
equal_value = CustomPortfolio(congressmen, prices_df, weighting='equal_value')
equal_value.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000          20      0.000000           0.000000   
1    2019-01-04  103442.415727          20      0.034424           0.034424   
2    2019-01-07  105294.569832          20      0.017905           0.052946   
3    2019-01-08  106726.967450          20      0.013604           0.067270   
4    2019-01-09  107159.208515          20      0.004050           0.071592   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  276094.581226          20     -0.009270           1.760946   
1562 2024-12-30  273066.768346          20     -0.010967           1.730668   
1563 2024-12-31  273066.768346          20      0.000000           1.730668   
1564 2025-01-01  273066.768346          20      0.000000           1.730668   
1565 2025-01-02  272960.943683          20     -0.000388           1.729609   

      cumulative_return_pct  log_return  cumulative_log_return  
0                  0.000000    0.000000               0.000000  
1                  3.442416    0.033845               0.033845  
2                  5.294570    0.017747               0.051592  
3                  6.726967    0.013512               0.065104  
4                  7.159209    0.004042               0.069145  
...                     ...         ...                    ...  
1561             176.094581   -0.009314               1.015573  
1562             173.066768   -0.011027               1.004546  
1563             173.066768    0.000000               1.004546  
1564             173.066768    0.000000               1.004546  
1565             172.960944   -0.000388               1.004159  

[1566 rows x 8 columns]

## Mean-Variance portfolio

In [63]:
mean_var = CustomPortfolio(congressmen, prices_df, weighting='mean_variance')
mean_var.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000          19  0.000000e+00           0.000000   
1    2019-01-04  102395.397525          19  2.395398e-02           0.023954   
2    2019-01-07  102882.126099          19  4.753422e-03           0.028821   
3    2019-01-08  103937.419038          19  1.025730e-02           0.039374   
4    2019-01-09  103408.160294          19 -5.092091e-03           0.034082   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  230961.373036          20 -9.270323e-03           1.309614   
1562 2024-12-30  228428.517024          20 -1.096658e-02           1.284285   
1563 2024-12-31  228428.517024          20 -3.330669e-16           1.284285   
1564 2025-01-01  228428.517024          20  0.000000e+00           1.284285   
1565 2025-01-02  228339.991530          20 -3.875413e-04           1.283400   

      cumulative_return_pct    log_return  cumulative_log_return  
0                  0.000000  0.000000e+00               0.000000  
1                  2.395398  2.367158e-02               0.023672  
2                  2.882126  4.742161e-03               0.028414  
3                  3.937419  1.020505e-02               0.038619  
4                  3.408160 -5.105099e-03               0.033514  
...                     ...           ...                    ...  
1561             130.961373 -9.313560e-03               0.837080  
1562             128.428517 -1.102715e-02               0.826053  
1563             128.428517 -3.330669e-16               0.826053  
1564             128.428517  0.000000e+00               0.826053  
1565             128.339992 -3.876165e-04               0.825666  

[1566 rows x 8 columns]

## Metrics and Comparison

In [64]:
def calculate_portfolio_metrics(history_df, risk_free_rate=None):

    if risk_free_rate is None:
        risk_free_rate = get_risk_free_rate()

    if history_df is None or history_df.empty:
        return {
            'annualized_return': 0,
            'volatility': 0,
            'sharpe_ratio': 0,
            'max_drawdown': 0
        }

    # Daily returns from log returns
    if 'log_return' in history_df.columns:
        daily_returns = history_df['log_return'].dropna()
    else:
        daily_returns = history_df['portfolio_value'].pct_change().dropna()

    # Annualized metrics (252 trading days)
    mean_daily_return = daily_returns.mean()
    std_daily_return = daily_returns.std()

    annualized_return = mean_daily_return * 252
    volatility = std_daily_return * np.sqrt(252)

    # Sharpe ratio
    if volatility > 0:
        sharpe_ratio = (annualized_return - risk_free_rate) / volatility
    else:
        sharpe_ratio = 0

    # Maximum drawdown
    if 'portfolio_value' in history_df.columns:
        cumulative = history_df['portfolio_value']
    else:
        cumulative = (1 + daily_returns).cumprod()

    running_max = cumulative.expanding().max()
    drawdown = (cumulative - running_max) / running_max
    max_drawdown = drawdown.min()

    return {
        'annualized_return': annualized_return * 100,  # as percentage
        'volatility': volatility * 100,
        'sharpe_ratio': sharpe_ratio,
        'max_drawdown': max_drawdown * 100
    }


def compare_all_portfolios(copycat_portfolios, custom_portfolios, spy_df, risk_free_rate=None):

    if risk_free_rate is None:
        risk_free_rate = get_risk_free_rate()

    results = []

    # Copycat portfolios
    for name, portfolio in copycat_portfolios.items():
        if hasattr(portfolio, 'history'):
            history = portfolio.history
        else:
            history = portfolio  # Assume it's already a DataFrame

        metrics = calculate_portfolio_metrics(history, risk_free_rate)
        metrics['name'] = name
        metrics['type'] = 'Copycat'
        results.append(metrics)

    # Custom portfolios
    for name, portfolio in custom_portfolios.items():
        if hasattr(portfolio, 'history'):
            history = portfolio.history
        else:
            history = portfolio

        metrics = calculate_portfolio_metrics(history, risk_free_rate)
        metrics['name'] = name
        metrics['type'] = 'Custom'
        results.append(metrics)

    # SPY benchmark
    spy_metrics = calculate_portfolio_metrics(spy_df, risk_free_rate)
    spy_metrics['name'] = 'SPY'
    spy_metrics['type'] = 'Benchmark'
    results.append(spy_metrics)

    # Create DataFrame
    df = pd.DataFrame(results)
    df = df[['name', 'type', 'annualized_return', 'volatility', 'sharpe_ratio', 'max_drawdown']]
    df.columns = ['Portfolio', 'Type', 'Ann. Return (%)', 'Volatility (%)', 'Sharpe Ratio', 'Max Drawdown (%)']

    # Sort by Sharpe ratio
    df = df.sort_values('Sharpe Ratio', ascending=False).reset_index(drop=True)

    return df


def print_comparison_table(comparison_df):
    """Print formatted comparison table."""
    print("\n" + "="*90)
    print("PORTFOLIO COMPARISON")
    print("="*90)
    print(f"\nRisk-Free Rate (3M T-Bill): {get_risk_free_rate()*100:.2f}%\n")
    print(comparison_df.to_string(index=False))
    print("\n" + "="*90)

In [65]:
equal_share_weight_10 = CustomPortfolio(congressmen, prices_df, weighting='equal_share_weight', n_stocks=10)
equal_share_weight_10.simulate()
equal_value_10 = CustomPortfolio(congressmen, prices_df, weighting='equal_value', n_stocks=10)
equal_value_10.simulate()
mean_var_10 = CustomPortfolio(congressmen, prices_df, weighting='mean_variance', n_stocks=10)
mean_var_10.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000           8  0.000000e+00           0.000000   
1    2019-01-04  103289.851460           8  3.289851e-02           0.032899   
2    2019-01-07  105155.526418           8  1.806252e-02           0.051555   
3    2019-01-08  106907.606339           8  1.666180e-02           0.069076   
4    2019-01-09  107057.688263           8  1.403847e-03           0.070577   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  275705.749758          10 -1.102064e-02           1.757057   
1562 2024-12-30  272571.619312          10 -1.136766e-02           1.725716   
1563 2024-12-31  272571.619312          10  2.220446e-16           1.725716   
1564 2025-01-01  272571.619312          10  0.000000e+00           1.725716   
1565 2025-01-02  272882.038493          10  1.138854e-03           1.728820   

      cumulative_return_pct    log_return  cumulative_log_return  
0                  0.000000  0.000000e+00               0.000000  
1                  3.289851  3.236894e-02               0.032369  
2                  5.155526  1.790133e-02               0.050270  
3                  6.907606  1.652451e-02               0.066795  
4                  7.057688  1.402863e-03               0.068198  
...                     ...           ...                    ...  
1561             175.705750 -1.108182e-02               1.014164  
1562             172.571619 -1.143277e-02               1.002731  
1563             172.571619  2.220446e-16               1.002731  
1564             172.571619  0.000000e+00               1.002731  
1565             172.882038  1.138206e-03               1.003869  

[1566 rows x 8 columns]

In [66]:
equal_share_weight_5 = CustomPortfolio(congressmen, prices_df, weighting='equal_share_weight', n_stocks=5)
equal_share_weight_5.simulate()
equal_value_5 = CustomPortfolio(congressmen, prices_df, weighting='equal_value', n_stocks=5)
equal_value_5.simulate()
mean_var_5 = CustomPortfolio(congressmen, prices_df, weighting='mean_variance', n_stocks=5)
mean_var_5.simulate()

Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000           5      0.000000           0.000000   
1    2019-01-04  104306.439584           5      0.043064           0.043064   
2    2019-01-07  107401.104973           5      0.029669           0.074011   
3    2019-01-08  110013.059924           5      0.024320           0.100131   
4    2019-01-09  110394.296200           5      0.003465           0.103943   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  307785.271069           5     -0.014981           2.077853   
1562 2024-12-30  303713.320404           5     -0.013230           2.037133   
1563 2024-12-31  303713.320404           5      0.000000           2.037133   
1564 2025-01-01  303713.320404           5      0.000000           2.037133   
1565 2025-01-02  306811.414211           5      0.010201           2.068114   

      cumulative_return_pct  log_return  cumulative_log_return  
0                  0.000000    0.000000               0.000000  
1                  4.306440    0.042163               0.042163  
2                  7.401105    0.029237               0.071400  
3                 10.013060    0.024029               0.095429  
4                 10.394296    0.003459               0.098888  
...                     ...         ...                    ...  
1561             207.785271   -0.015094               1.124232  
1562             203.713320   -0.013318               1.110914  
1563             203.713320    0.000000               1.110914  
1564             203.713320    0.000000               1.110914  
1565             206.811414    0.010149               1.121063  

[1566 rows x 8 columns]

In [67]:
custom_dict = {
    'Top20_EqualShare': equal_share_weight,
    'Top20_EqualValue': equal_value,
    'Top20_MeanVar': mean_var,
    'Top10_EqualShare': equal_share_weight_10,
    'Top10_EqualValue': equal_value_10,
    'Top10_MeanVar': mean_var_10,
    'Top5_EqualShare': equal_share_weight_5,
    'Top5_EqualValue': equal_value_5,
    'Top5_MeanVar': mean_var_5,
}

In [68]:
comparison = compare_all_portfolios(copycat_objects, custom_dict, spy_returns)
print(comparison)


                   Portfolio       Type  Ann. Return (%)  Volatility (%)  \
0            Earl Blumenauer    Copycat        38.047423       27.588878   
1               Lois Frankel    Copycat        28.982107       30.565003   
2                  Susie Lee    Copycat        63.127672       74.384705   
3            Josh Gottheimer    Copycat        32.245267       36.481104   
4                 Kevin Hern    Copycat       149.633862      206.401011   
5              Pete Sessions    Copycat        20.260652       24.432006   
6             Mikie Sherrill    Copycat        88.451910      126.062521   
7           Top10_EqualValue     Custom        18.857488       22.909434   
8               Nancy Pelosi    Copycat        52.344227       73.993425   
9                        SPY  Benchmark        16.196369       19.889098   
10          Top20_EqualValue     Custom        16.158873       20.308767   
11       Carol Devine Miller    Copycat        41.182143       61.911023   
12          

In [69]:
comparison.to_csv(sep="\t", index=False)


'Portfolio\tType\tAnn. Return (%)\tVolatility (%)\tSharpe Ratio\tMax Drawdown (%)\r\nEarl Blumenauer\tCopycat\t38.04742323367476\t27.588877856639392\t1.249033155810436\t-23.755932004873586\r\nLois Frankel\tCopycat\t28.982106832087272\t30.565002527221285\t0.8308229894744291\t-31.200562916185405\r\nSusie Lee\tCopycat\t63.127672130931344\t74.38470463054867\t0.8004289640931302\t-51.27526966288113\r\nJosh Gottheimer\tCopycat\t32.24526692696723\t36.48110401335207\t0.7855372704003386\t-36.00137765283255\r\nKevin Hern\tCopycat\t149.6338622007403\t206.4010106508961\t0.7075830766576648\t-131.2692981640427\r\nPete Sessions\tCopycat\t20.26065203149082\t24.432006169350284\t0.6824102718702935\t-22.72455822332723\r\nMikie Sherrill\tCopycat\t88.45190951087719\t126.0625214420328\t0.6731890531855835\t-48.674939133982306\r\nTop10_EqualValue\tCustom\t18.857488145866448\t22.909434431464533\t0.6665152792147087\t-39.15069066757193\r\nNancy Pelosi\tCopycat\t52.344226629917465\t73.99342494686145\t0.65892647361

## Visualization

In [70]:
def plot_custom_portfolios_comparison(custom_portfolios_dict, spy_df, save_path=None):

    fig = make_subplots(
        rows=2, cols=1,
        subplot_titles=('Cumulative Return (%)', 'Cumulative Log Return'),
        vertical_spacing=0.12
    )

    color_list = px.colors.qualitative.T10
    portfolio_names = list(custom_portfolios_dict.keys())
    colors = {name: color_list[i % len(color_list)] for i, name in enumerate(portfolio_names)}

    # Top plot: Cumulative Returns
    for name, portfolio in custom_portfolios_dict.items():
        if hasattr(portfolio, 'history'):
            history = portfolio.history
        else:
            history = portfolio

        if history is None or history.empty:
            continue

        fig.add_trace(go.Scatter(
            x=history['Date'],
            y=history['cumulative_return_pct'],
            mode='lines',
            name=f'{name} (Return %)',
            line=dict(width=2, color=colors.get(name, '#333'))
        ), row=1, col=1)

    # SPY cumulative returns
    fig.add_trace(go.Scatter(
        x=spy_df['Date'],
        y=spy_df['cumulative_return_pct'],
        mode='lines',
        name='SPY (Return %)',
        line=dict(width=2, dash='dash', color='gray')
    ), row=1, col=1)

    # Bottom plot: Log Returns
    for name, portfolio in custom_portfolios_dict.items():
        if hasattr(portfolio, 'history'):
            history = portfolio.history
        else:
            history = portfolio

        if history is None or history.empty or 'cumulative_log_return' not in history.columns:
            continue

        fig.add_trace(go.Scatter(
            x=history['Date'],
            y=history['cumulative_log_return'],
            mode='lines',
            name=f'{name} (Log)',
            line=dict(width=2, color=colors.get(name, '#333'))
        ), row=2, col=1)

    # SPY log returns
    fig.add_trace(go.Scatter(
        x=spy_df['Date'],
        y=spy_df['cumulative_log_return'],
        mode='lines',
        name='SPY (Log)',
        line=dict(width=2, dash='dash', color='gray')
    ), row=2, col=1)

    # Layout
    fig.update_layout(
        title='Custom Portfolios vs SPY',
        template='plotly_white',
        height=700,
        legend=dict(
            x=1.02, y=1,  # move legend outside
            font=dict(size=10)
        ),
        hovermode='x unified'
    )
    fig.update_xaxes(title_text='Date', row=2, col=1)
    fig.update_yaxes(title_text='Cumulative Return (%)', row=1, col=1)
    fig.update_yaxes(title_text='Cumulative Log Return', row=2, col=1)


    filename = "CustomPortfolio.html"
    if save_path:
      fig.write_html(os.path.join(save_path, filename))

    return fig


In [71]:
fig = plot_custom_portfolios_comparison(custom_dict, spy_returns, save_path=summary_dir)
fig.show()



In [72]:
test = equal_share_weight.get_portfolio_composition('2023-01-15')
print(test)


Portfolio Composition - 2023-01-15
Weighting: equal_share_weight, Rebalance: quarterly
Total Value:         $165,417.01
Number of Positions: 20

   Asset   Type     Shares       Price         Value  Weight (%)
0   COST  Stock  53.228668  465.094910  24756.382623       14.97
1    UNH  Stock  53.228668  463.460205  24669.369475       14.91
2     HD  Stock  53.228668  306.887695  16335.223305        9.88
3    ROK  Stock  53.228668  270.806335  14414.660573        8.71
4    ACN  Stock  53.228668  270.588409  14403.060661        8.71
5   MSFT  Stock  53.228668  233.111725  12408.226653        7.50
6    TXN  Stock  53.228668  162.388947   8643.747352        5.23
7    JNJ  Stock  53.228668  157.473709   8382.115810        5.07
8    JPM  Stock  53.228668  133.200287   7090.073872        4.29
9   CRWD  Stock  53.228668   99.529999   5297.849280        3.20
10   TIP  Stock  53.228668   99.146294   5277.425166        3.19
11   EMR  Stock  53.228668   91.929985   4893.310671        2.96
12   RTX 

In [73]:
test2 = equal_value.get_portfolio_composition('2023-01-15')
print(test2)


Portfolio Composition - 2023-01-15
Weighting: equal_value, Rebalance: quarterly
Total Value:         $191,052.74
Number of Positions: 20

   Asset   Type       Shares       Price         Value  Weight (%)
0    NGL  Stock  7512.288393    1.550000  11644.046652        6.09
1     AB  Stock   349.416237   29.541569  10322.303778        5.40
2   PYPL  Stock   127.925896   79.296692  10144.100351        5.31
3    ROK  Stock    37.171830  270.806335  10066.367144        5.27
4    TXN  Stock    60.647904  162.388947   9848.549199        5.15
5      T  Stock   591.462864   16.555771   9792.123658        5.13
6    JPM  Stock    73.313882  133.200287   9765.430107        5.11
7     ET  Stock  1001.690822    9.686118   9702.495629        5.08
8   COST  Stock    20.774991  465.094910   9662.342340        5.06
9    ACN  Stock    35.664408  270.588409   9650.375562        5.05
10    HD  Stock    31.058968  306.887695   9531.615002        4.99
11  DGRO  Stock   195.158295   47.890369   9346.202856   

In [74]:
test3 = equal_value.get_portfolio_composition('2019-05-31')
print(test3)


Portfolio Composition - 2019-05-31
Weighting: equal_value, Rebalance: quarterly
Total Value:         $115,492.24
Number of Positions: 20

   Asset   Type      Shares       Price        Value  Weight (%)
0   TTWO  Stock   61.704569  108.150002  6673.349217        5.78
1    PGR  Stock   98.577694   65.051376  6412.614691        5.55
2   MSFT  Stock   52.664438  116.379555  6129.063896        5.31
3     SO  Stock  147.873307   41.238453  6098.066416        5.28
4   TDOC  Stock  104.731304   58.119999  6086.983267        5.27
5    CDW  Stock   65.504624   91.058037  5964.722479        5.16
6    BEP  Stock  454.970107   13.099221  5959.754080        5.16
7   DXCM  Stock  195.568779   30.325001  5930.623385        5.14
8    TTD  Stock  294.168240   19.881001  5848.358932        5.06
9   MIDD  Stock   44.782438  130.470001  5842.764715        5.06
10  AMZN  Stock   65.400089   88.753502  5804.486931        5.03
11     T  Stock  403.262473   14.380514  5799.121700        5.02
12   EPD  Stock 

In [75]:
test4 = mean_var.get_portfolio_composition('2023-01-15')
print(test4)


Portfolio Composition - 2023-01-15
Weighting: mean_variance, Rebalance: quarterly
Total Value:         $159,821.33
Number of Positions: 20

   Asset   Type       Shares       Price        Value  Weight (%)
0    NGL  Stock  6284.253875    1.550000  9740.593207        6.09
1     AB  Stock   292.297130   29.541569  8634.915770        5.40
2   PYPL  Stock   107.013837   79.296692  8485.843275        5.31
3    ROK  Stock    31.095348  270.806335  8420.817123        5.27
4    TXN  Stock    50.733785  162.388947  8238.605899        5.15
5      T  Stock   494.776372   16.555771  8191.404246        5.13
6    JPM  Stock    61.329255  133.200287  8169.074293        5.11
7     ET  Stock   837.944326    9.686118  8116.427720        5.08
8   COST  Stock    17.378901  465.094910  8082.838293        5.06
9    ACN  Stock    29.834344  270.588409  8072.827725        5.05
10    HD  Stock    25.981755  306.887695  7973.480966        4.99
11  DGRO  Stock   163.255750   47.890369  7818.378161        4.89
1

In [76]:
for k in custom_dict.keys():
  print(f"History for {k} Portfolio")
  print("\n")
  print(custom_dict[k].history)
  print("\n")
  print("-------------------------")

History for Top20_EqualShare Portfolio


           Date    stock_value  n_holdings  daily_return  cumulative_return  \
0    2019-01-03  100000.000000          20  0.000000e+00           0.000000   
1    2019-01-04  103338.371533          20  3.338372e-02           0.033384   
2    2019-01-07  104716.937406          20  1.334031e-02           0.047169   
3    2019-01-08  106015.324823          20  1.239902e-02           0.060153   
4    2019-01-09  106134.660088          20  1.125642e-03           0.061347   
...         ...            ...         ...           ...                ...   
1561 2024-12-27  228848.470891          20 -1.064992e-02           1.288485   
1562 2024-12-30  226122.268280          20 -1.191270e-02           1.261223   
1563 2024-12-31  226122.268280          20  2.220446e-16           1.261223   
1564 2025-01-01  226122.268280          20  0.000000e+00           1.261223   
1565 2025-01-02  225544.580750          20 -2.554757e-03           1.255446   

      cumu

In [77]:
def get_value_asof(df, date, value_col):
    date = pd.to_datetime(date)
    df = df.sort_values("Date")

    sub = df[df["Date"] <= date]
    if sub.empty:
        return np.nan

    return sub.iloc[-1][value_col]

rows = {}

# ---- PORTFOLIOS ----
for name, portfolio in custom_dict.items():
    history = portfolio.history.copy()
    row = {}

    for date_str in SNAPSHOT_DATES:
        row[date_str] = get_value_asof(
            history,
            date_str,
            "cumulative_return_pct"
        )

    rows[name] = row


# ---- SPY BENCHMARK (SAME METRIC) ----
spy_row = {}

for date_str in SNAPSHOT_DATES:
    spy_row[date_str] = get_value_asof(
        spy_returns,
        date_str,
        "cumulative_return_pct"
    )

rows["SPY"] = spy_row


snapshot_return_table = pd.DataFrame(rows).T.round(2)
snapshot_return_table





2019-01-03  2019-12-31  2020-12-31  2021-12-31  2022-12-31  \
Top20_EqualShare         0.0       29.92       64.98      105.10       61.41   
Top20_EqualValue         0.0       34.21       63.39      112.67       81.80   
Top20_MeanVar            0.0       29.69       49.14       77.91       52.08   
Top10_EqualShare         0.0       23.17       66.80       99.19       53.50   
Top10_EqualValue         0.0       39.69       74.99      134.96       87.73   
Top10_MeanVar            0.0       30.63       56.27       98.62       58.70   
Top5_EqualShare          0.0       27.89       63.33       82.19        5.07   
Top5_EqualValue          0.0       47.87       81.53      145.18       84.09   
Top5_MeanVar             0.0       40.83       72.88      145.73       84.51   
SPY                      0.0       34.29       58.91      104.56       67.38   

                  2023-12-31  2024-12-31  2025-01-02  
Top20_EqualShare       94.07      126.12      125.54  
Top20_EqualValue      125.90      173.07      172.96  
Top20_MeanVar          88.97      128.43      128.34  
Top10_EqualShare       93.33      132.61      132.64  
Top10_EqualValue      161.68      222.43      222.80  
Top10_MeanVar         121.21      172.57      172.88  
Top5_EqualShare        48.11       97.57       99.98  
Top5_EqualValue       137.51      203.03      206.12  
Top5_MeanVar          138.05      203.71      206.81  
SPY                   111.20      163.76      163.76

In [78]:
snapshot_return_table.describe()


2019-01-03  2019-12-31  2020-12-31  2021-12-31  2022-12-31  2023-12-31  \
count        10.0   10.000000   10.000000   10.000000   10.000000   10.000000   
mean          0.0   33.819000   65.222000  110.611000   63.627000  112.003000   
std           0.0    7.244944    9.475727   24.138008   24.662463   32.246457   
min           0.0   23.170000   49.140000   77.910000    5.070000   48.110000   
25%           0.0   29.747500   60.015000   98.762500   54.800000   93.515000   
50%           0.0   32.420000   64.185000  104.830000   64.395000  116.205000   
75%           0.0   38.340000   71.360000  129.387500   83.517500  134.607500   
max           0.0   47.870000   81.530000  145.730000   87.730000  161.680000   

       2024-12-31  2025-01-02  
count   10.000000   10.000000  
mean   162.330000  163.183000  
std     40.470242   40.892225  
min     97.570000   99.980000  
25%    129.475000  129.415000  
50%    168.165000  168.320000  
75%    195.540000  197.830000  
max    222.430000  222.800000

# Back-Testing

In [89]:
def get_copycats_beating_spy(comparison_df):

    spy_sharpe = comparison_df.loc[
        comparison_df['Type'] == 'Benchmark', 'Sharpe Ratio'
    ].values[0]

    copycats = comparison_df[comparison_df['Type'] == 'Copycat']
    beating = copycats[copycats['Sharpe Ratio'] > spy_sharpe]

    names = beating['Portfolio'].tolist()
    print(f"  SPY in-sample Sharpe Ratio: {spy_sharpe:.4f}")
    print(f"  Copycat portfolios beating SPY: {len(names)}/{len(copycats)}")
    for n in names:
        sr = beating.loc[beating['Portfolio'] == n, 'Sharpe Ratio'].values[0]
        print(f"    {n:30s}  Sharpe = {sr:.4f}")

    return names


In [90]:
def plot_backtest_results(backtest_results, spy_bt, save_path=None):
    """Plot cumulative return (%) for all back-tested portfolios vs SPY."""
    fig = go.Figure()

    colors = [
        '#1f77b4', '#ff7f0e', '#2ca02c', '#d62728', '#9467bd',
        '#8c564b', '#e377c2', '#7f7f7f', '#bcbd22', '#17becf',
        '#aec7e8', '#ffbb78', '#98df8a', '#ff9896', '#c5b0d5',
        '#c49c94', '#f7b6d2', '#c7c7c7', '#dbdb8d', '#9edae5',
        '#393b79', '#637939', '#8c6d31', '#843c39', '#7b4173',
    ]

    for i, (name, df) in enumerate(backtest_results.items()):
        if df is None or df.empty:
            continue
        fig.add_trace(go.Scatter(
            x=df['Date'],
            y=df['cumulative_return_pct'],
            mode='lines',
            name=name,
            line=dict(width=1.5, color=colors[i % len(colors)]),
        ))

    # SPY benchmark
    if spy_bt is not None and not spy_bt.empty:
        fig.add_trace(go.Scatter(
            x=spy_bt['Date'],
            y=spy_bt['cumulative_return_pct'],
            mode='lines',
            name='SPY',
            line=dict(width=3, color='black', dash='dash'),
        ))

    fig.update_layout(
        title='Back-Test: All Portfolios vs SPY '
              f'({BACKTEST_START_DATE} → {BACKTEST_END_DATE})',
        xaxis_title='Date',
        yaxis_title='Cumulative Return (%)',
        template='plotly_white',
        legend=dict(x=1.02, y=1, font=dict(size=9)),
        hovermode='x unified',
        height=800,
        width=1300,
    )

    if save_path:
        fig.write_html(save_path)
        print(f"  Saved plot → {save_path}")

    return fig


def print_metrics_table(metrics_rows):
    """Print a formatted comparison table."""
    df = pd.DataFrame(metrics_rows)
    df = df[['Portfolio', 'Type',
             'Ann. Return (%)', 'Volatility (%)',
             'Sharpe Ratio', 'Max Drawdown (%)']]
    df = df.sort_values('Sharpe Ratio', ascending=False).reset_index(drop=True)

    rfr = get_risk_free_rate()
    print("\n" + "=" * 100)
    print("BACK-TEST PORTFOLIO COMPARISON")
    print("=" * 100)
    print(f"\nRisk-Free Rate: {rfr * 100:.2f}%")
    print(f"Back-Test Period: {BACKTEST_START_DATE} → {BACKTEST_END_DATE}\n")
    print(df.to_string(index=False))
    print("\n" + "=" * 100)
    return df



In [91]:
selected_copycats = get_copycats_beating_spy(comparison)

  SPY in-sample Sharpe Ratio: 0.6339
  Copycat portfolios beating SPY: 8/20
    Earl Blumenauer                 Sharpe = 1.2490
    Lois Frankel                    Sharpe = 0.8308
    Susie Lee                       Sharpe = 0.8004
    Josh Gottheimer                 Sharpe = 0.7855
    Kevin Hern                      Sharpe = 0.7076
    Pete Sessions                   Sharpe = 0.6824
    Mikie Sherrill                  Sharpe = 0.6732
    Nancy Pelosi                    Sharpe = 0.6589


In [93]:
CUSTOM_PORTFOLIO_CONFIGS = [
    ('equal_share', 5,  'Top5_EqualShare'),
    ('equal_share', 10, 'Top10_EqualShare'),
    ('equal_share', 20, 'Top20_EqualShare'),
    ('equal_value', 5,  'Top5_EqualValue'),
    ('equal_value', 10, 'Top10_EqualValue'),
    ('equal_value', 20, 'Top20_EqualValue'),
    ('mean_variance', 5,  'Top5_MeanVariance'),
    ('mean_variance', 10, 'Top10_MeanVariance'),
    ('mean_variance', 20, 'Top20_MeanVariance'),
]


In [ ]:
print(f"\nRunning back-test simulations "
        f"({BACKTEST_START_DATE} → {BACKTEST_END_DATE})...")

backtest_results = {}  # name → history DataFrame

# 5a. Copycat portfolios — re-simulate over back-test period
print("\n  --- Copycat portfolios (beating SPY) ---")
for name in selected_copycats:
    if name not in congressmen_by_name:
        print(f"    {name}: not found in lawmakers, skipping")
        continue

    congressman = congressmen_by_name[name]
    if congressman.transactions is None:
        print(f"    {name}: no transactions, skipping")
        continue

    print(f"    Simulating: {name}")
    cp = CopycatPortfolio(congressman, prices_df)
    hist = cp.simulate(start_date=BACKTEST_START_DATE,
                        end_date=BACKTEST_END_DATE)

    if hist is not None and len(hist) > 0:
        # CopycatPortfolio history uses stock_value but may not have
        # daily_return in the same format as CustomPortfolio.
        # Add it for consistent metrics calculation.
        if 'daily_return' not in hist.columns:
            hist = hist.copy()
            hist['daily_return'] = hist['stock_value'].pct_change().fillna(0)
            hist['cumulative_return'] = (
                (1 + hist['daily_return']).cumprod() - 1
            )
            hist['cumulative_return_pct'] = hist['cumulative_return'] * 100
        backtest_results[name] = hist

print(f"  Simulated {len(backtest_results)} copycat portfolios")

# 5b. Custom (simulated) portfolios — re-simulate over back-test period
print("\n  --- Custom (simulated) portfolios ---")
for weighting, n_stocks, label in CUSTOM_PORTFOLIO_CONFIGS:
    print(f"    Simulating: {label}")
    portfolio = CustomPortfolio(
        congressmen, prices_df,
        rebalance_freq='quarterly',
        n_stocks=n_stocks,
        weighting=weighting,
    )
    hist = portfolio.simulate(start_date=BACKTEST_START_DATE,
                                end_date=BACKTEST_END_DATE)
    if hist is not None and len(hist) > 0:
        backtest_results[label] = hist

print(f"\n  Total back-tested portfolios: {len(backtest_results)}")

# SPY benchmark for back-test period
spy_bt = get_spy_returns(start_date=BACKTEST_START_DATE,
                            end_date=BACKTEST_END_DATE)


[5/6] Running back-test simulations (2025-01-03 → 2025-12-31)...

  --- Copycat portfolios (beating SPY) ---
    Simulating: Earl Blumenauer
    Initial positions: 58 tickers
    No transactions in date range
    Simulating: Lois Frankel
    Initial positions: 53 tickers
    No transactions in date range
    Simulating: Susie Lee
    Initial positions: 115 tickers
    Transactions in range: 18
    Simulating: Josh Gottheimer
    Initial positions: 151 tickers
    Transactions in range: 418
    Simulating: Kevin Hern
    Initial positions: 86 tickers
    Transactions in range: 22
    Simulating: Pete Sessions
    Initial positions: 25 tickers
    Transactions in range: 2
    Simulating: Mikie Sherrill
    Initial positions: 10 tickers
    Transactions in range: 1
    Simulating: Nancy Pelosi
    Initial positions: 6 tickers
    Transactions in range: 3
  Simulated 8 copycat portfolios

  --- Custom (simulated) portfolios ---
    Simulating: Top5_EqualShare
    Simulating: Top10_EqualSh

In [95]:
rfr = get_risk_free_rate()

# Build metrics table
metrics_rows = []
for name, hist in backtest_results.items():
    m = calculate_portfolio_metrics(hist, risk_free_rate=rfr)
    ptype = 'Copycat' if name in selected_copycats else 'Custom'
    metrics_rows.append({
        'Portfolio': name,
        'Type': ptype,
        'Ann. Return (%)': round(m['annualized_return'], 2),
        'Volatility (%)': round(m['volatility'], 2),
        'Sharpe Ratio': round(m['sharpe_ratio'], 4),
        'Max Drawdown (%)': round(m['max_drawdown'], 2),
    })

# SPY metrics
spy_m = calculate_portfolio_metrics(spy_bt, risk_free_rate=rfr)
metrics_rows.append({
    'Portfolio': 'SPY',
    'Type': 'Benchmark',
    'Ann. Return (%)': round(spy_m['annualized_return'] , 2),
    'Volatility (%)': round(spy_m['volatility'], 2),
    'Sharpe Ratio': round(spy_m['sharpe_ratio'], 4),
    'Max Drawdown (%)': round(spy_m['max_drawdown'], 2),
})

comparison_bt = print_metrics_table(metrics_rows)


BACK-TEST PORTFOLIO COMPARISON

Risk-Free Rate: 3.59%
Back-Test Period: 2025-01-03 → 2025-12-31

         Portfolio      Type  Ann. Return (%)  Volatility (%)  Sharpe Ratio  Max Drawdown (%)
               SPY Benchmark            16.32           19.35        0.6580            -19.21
    Mikie Sherrill   Copycat            11.29           18.90        0.4077            -16.44
     Pete Sessions   Copycat            10.80           18.80        0.3837            -12.76
Top20_MeanVariance    Custom             9.44           15.88        0.3686            -16.25
  Top20_EqualValue    Custom             9.44           15.88        0.3686            -16.25
  Top20_EqualShare    Custom             9.44           15.88        0.3686            -16.25
         Susie Lee   Copycat            12.36           24.27        0.3615            -17.55
   Josh Gottheimer   Copycat            10.39           24.31        0.2797            -15.79
Top10_MeanVariance    Custom             9.53           

In [96]:
# Save metrics to CSV
csv_path = os.path.join(BACKTEST_OUTPUT_DIR, 'backtest_metrics.csv')
comparison_bt.to_csv(csv_path, index=False)
print(f"  Saved metrics → {csv_path}")

# Plot cumulative returns
plot_path = os.path.join(BACKTEST_OUTPUT_DIR,
                            'backtest_cumulative_returns.html')
plot_backtest_results(backtest_results, spy_bt, save_path=plot_path)

  Saved metrics → c:\Users\Aaron\Documents\Projects\WQU\Capston_Project\Congress_Trading\output/backtest/backtest_metrics.csv
  Saved plot → c:\Users\Aaron\Documents\Projects\WQU\Capston_Project\Congress_Trading\output/backtest/backtest_cumulative_returns.html
